# 21_5 Descriptive Analysis - Stations

Let us now take a closer look on the characterisitcs of our aggregrated data.

In [1]:
# import libraries
import pandas as pd
import numpy as np
import sklearn
from datetime import datetime
import os
import geopandas as gpd
import matplotlib.pyplot as plt
import folium
import shapely
import hashlib
import holidays
from shapely import Point, wkt
import scipy.stats
import seaborn as sns

## Load and prepare data

In [2]:
data_month_double = '07'

In [3]:
# read final data
data = pd.read_csv("../Data/20_Final_Data.csv")

/tmp/ipykernel_385708/974816303.py:2: DtypeWarning: Columns (28) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv("../../../20_Final_Data_NEW_TEST.csv")


In [4]:
tier = pd.read_parquet("../Data/12_tier_part2.parquet")
next = pd.read_parquet("../Data/15_nextbike_part2.parquet")

In [5]:
tier['trip_duration_seconds'] = tier['trip_duration'].dt.total_seconds()
next['trip_duration_seconds'] = next['trip_duration'].dt.total_seconds()

In [6]:
# transform geometry
data['station_point'] = data['station_point'].apply(wkt.loads)

In [7]:
data['buffer_zone'] = shapely.wkt.loads(data['buffer_zone'])

In [8]:
data = gpd.GeoDataFrame(data, geometry='station_point')

In [9]:
data = data.loc[:, ~data.columns.str.contains('Unnamed')]

In [10]:
#data.drop(columns=['Unnamed: 0', 'Unnamed: 0.1', 'Unnamed: 0.2'], inplace=True)

In [11]:
data['actual_arrival_time'] = pd.to_datetime(data['actual_arrival_time'])
data['actual_departure_time'] = pd.to_datetime(data['actual_departure_time'])
data['scheduled_arrival_time'] = pd.to_datetime(data['scheduled_arrival_time'])
data['scheduled_departure_time'] = pd.to_datetime(data['scheduled_departure_time'])

In [12]:
data = gpd.GeoDataFrame(data, geometry='buffer_zone')

In [13]:
data.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 2564861 entries, 0 to 2564860
Data columns (total 56 columns):
 #   Column                               Dtype         
---  ------                               -----         
 0   route_id                             int64         
 1   agency_id                            int64         
 2   route_short_name                     object        
 3   route_type                           int64         
 4   route_type_name                      object        
 5   agency_name                          object        
 6   service_id                           int64         
 7   trip_id                              object        
 8   trip_headsign                        object        
 9   direction_id                         int64         
 10  shape_id                             int64         
 11  stop_id                              int64         
 12  actual_arrival_time                  datetime64[ns]
 13  actual_departure_ti

In [14]:
data['date'] = pd.to_datetime(data['date'])

In [15]:
data['arrival_delay'] = pd.to_timedelta(data['arrival_delay'])
data['departure_delay'] = pd.to_timedelta(data['departure_delay'])

In [16]:
data['arrival_delay_float'] = data['arrival_delay'].astype(str)
data['arrival_delay_float'] = data['arrival_delay_float'].str.split(' ', n=2).str[-1]
data['arrival_delay_float'] = data['arrival_delay_float'].astype(str)
data['arrival_delay_float'] = pd.to_timedelta(data['arrival_delay_float'])
data['arrival_delay_float'] = pd.to_timedelta(data['arrival_delay_float']).dt.total_seconds() / 60

In [17]:
data['departure_delay_float'] = data['departure_delay'].astype(str)
data['departure_delay_float'] = data['departure_delay_float'].str.split(' ', n=2).str[-1]
data['departure_delay_float'] = data['departure_delay_float'].astype(str)
data['departure_delay_float'] = pd.to_timedelta(data['departure_delay_float'])
data['departure_delay_float'] = pd.to_timedelta(data['departure_delay_float']).dt.total_seconds() / 60

In [18]:

#NEW FEATURES
data['delay_category'] = data['arrival_delay'].apply(lambda x: 1 if x > pd.Timedelta(0) else 0 if x == pd.Timedelta(0) else -1)
data['cancelled_trip'] = np.where((data['scheduled_arrival_time'].notna() & data['actual_arrival_time'].isna() & data['scheduled_departure_time'].notna() & data['actual_departure_time'].isna()), 1, 0)

## Data Description

### Definition of functions

In [19]:
def calc_stats(data, column_name):

    #generated by Copilot

    rows = len(data.index)

    sum = data[column_name].sum()

#Central Tendency

    # Calculate mean (average)
    mean = data[column_name].mean()
    # Calculate median (middle value)
    median = data[column_name].median()
    # Calculate mode (most frequent value)
    mode = data[column_name].mode()
    #calc maximum
    max = data[column_name].max()
    #calc minimum
    min = data[column_name].min()

    # Calculate range
    data_range = data[column_name].max() - data[column_name].min()
    # Calculate coefficient of variation of range
    cvr = data_range / mean
    # Calculate coefficient of variation of mean
    cvm = mean / mean
    # Calculate coefficient of variation of median
    cvmed = median / mean
    # Calculate coefficient of variation of mode
    cvmode = mode / mean
    # Calculate coefficient of variation of standard deviation
   

# Variability
# Measure of how spread out the values in a data set are
    
    # Calculate standard deviation (average amount of variability in a dataset; tells how far each score lies from the mean; the larger the standard deviation, the more variable the data)
    std_dev = data[column_name].std()
    # Calculate variance (average squared deviation from the mean; square of standard deviation; units of varriance are much larger than those of a typical value in the dataset)
    variance = data[column_name].var()
    # Calculate coefficient of variation
    cv = std_dev / mean # standard deviation divided by the mean; measures the relative variability of a dataset; allows comparison of variability of datasets with different units of measurement
    # Calculate 25th percentile
    percentile_25 = data[column_name].quantile(0.25)
    # Calculate 75th percentile
    percentile_75 = data[column_name].quantile(0.75)
    # Calculate interquartile range
    iqr = percentile_75 - percentile_25 # difference between the 75th and 25th percentiles; measures the spread of the middle 50% of values in a dataset
    # Calculate coefficient of quartile deviation
    qd = iqr / (percentile_75 + percentile_25)
    # Calculate coefficient of variation of coefficient of variation
    cvcv = std_dev / mean
    # Calculate coefficient of variation of coefficient of quartile deviation
    cvqd = iqr / (percentile_75 + percentile_25)
    # Calculate coefficient of variation of range

#Measure of Shape

    # Calculate skewness - measure of how much the probability distribution of a random variable deviates from the normal distribution
    skewness = data[column_name].skew()
    
    # Calculate kurtosis
    kurtosis = data[column_name].kurtosis()

    # Calculate coefficient of skewness
    cs = skewness / std_dev
    # Calculate coefficient of kurtosis
    ck = kurtosis / std_dev
    # Calculate coefficient of variation of skewness
    cvs = skewness / std_dev
    # Calculate coefficient of variation of kurtosis
    cvk = kurtosis / std_dev
    # Calculate coefficient of variation of coefficient of skewness
    cvcs = skewness / std_dev
    # Calculate coefficient of variation of coefficient of kurtosis
    cvck = kurtosis / std_dev
    
    
    
    #return "column: " + str(column_name), "mean: " + str(mean), "median: " + str(median), "mode: " + str(mode), "std_dev: " + str(std_dev), "variance: " + str(variance), "skewness: "+ str(skewness), "kurtosis: " + str(kurtosis), "percentile_25: "+ str(percentile_25), "percentile_75: "+ str(percentile_75), "iqr: " + str(iqr), "range: "+ str(data_range), "cv"+ str(cv), "qd: "+str(qd), "cs: "+ str(cs), "ck: " + str(ck), "csv: "+ str(cvs), "cvk: "+ str(cvk), "cvcs: "+ str(cvcs), "cvck: " +str(cvck), "cvcv: "+ str(cvcv), "cvqd: "+ str (cvqd), "cvr: "+ str(cvr), "cvm: " + str(cvm), "cvmed: " + str(cvmed), "cvmode: "+ str(cvmode)

    return pd.DataFrame({'column': [column_name],
                            'rows': [rows],
                         'sum': [sum],
                         'mean': [mean],
                         'median': [median],
                         'mode': [mode],
                         'max': [max],
                         'min': [min],
                         'std_dev': [std_dev],
                         'variance': [variance],
                         'skewness': [skewness],
                         'kurtosis': [kurtosis],
                         'percentile_25': [percentile_25],
                         'percentile_75': [percentile_75],
                         'iqr': [iqr],
                         'range': [data_range],
                         'cv': [cv],
                         'qd': [qd],
                         'cs': [cs],
                         'ck': [ck],
                         'cvs': [cvs],
                         'cvk': [cvk],
                         'cvcs': [cvcs],
                         'cvck': [cvck],
                         'cvcv': [cvcv],
                         'cvqd': [cvqd],
                         'cvr': [cvr],
                         'cvm': [cvm],
                         'cvmed': [cvmed],
                         'cvmode': [cvmode]}).T

In [20]:
# create a shorter dataframe with most interesting columns - for better overview
def show_short_df(dataframe):
    delay_short = dataframe[['route_id', 'trip_id', 'stop_id', 'stop_name', 'scheduled_arrival_time', 'actual_arrival_time', 'scheduled_departure_time', 'actual_departure_time', 'arrival_delay', 'departure_delay', 'tier_trips_count', 'tier_trips_end_at_station_count', 'nextbike_trips_count', 'nextbike_trips_end_at_station_count', 'buffer_zone', 'arrival_delay_float', 'departure_delay_float']]
    return delay_short

In [21]:
# transform geometry
point_start = gpd.GeoDataFrame(geometry=gpd.GeoSeries.from_wkb(tier["start_location"], crs=4326))
point_end = gpd.GeoDataFrame(geometry=gpd.GeoSeries.from_wkb(tier["end_location"], crs=4326))
# drop geometry columns in wrong format
tier = tier.drop(columns=["start_location", "end_location"])
# replace geometry columns with correct format
tier['start_location'] = point_start
tier['end_location'] = point_end

In [22]:
# get the data from the tier / nextbike dataset
def check_micromobility_datasets(type, data):
    
    if type == 'tier':

        return_data = tier.copy()
        return_data = return_data.iloc[0:0] # empty dataframe

        for item in data['tier_trips_id'].str.split(' ').explode().dropna():   # iterate over all tier ids in the dataframe
            
            id = tier[tier['tier_trips_id'] == int(float(item))]   # get the rows with the specific id
            return_data = pd.concat([return_data, id])  # add the rows to the return dataframe

            return_data.drop_duplicates(inplace=True)
            
    if type == 'next':

        return_data = next.copy()
        return_data = return_data.iloc[0:0] # empty dataframe

        for item in data['nextbike_trips_id'].str.split(' ').explode().dropna():   # iterate over all nextbike ids in the dataframe
            
            id = next[next['nextbike_trips_id'] == int(float(item))]  # get the rows with the specific id
            return_data = pd.concat([return_data, id]) # add the rows to the return dataframe

            return_data.drop_duplicates(inplace=True)

    return return_data

In [23]:
def get_station_to_station(data):
    t = check_micromobility_datasets('tier', data)
    n = check_micromobility_datasets('nextbike', data)

    t = t[t['end_stop_id'].notna() & t['start_stop_id'].notna()]
    n = n[n['end_stop_id'].notna() & n['start_stop_id'].notna()]
    
    return t, n

In [24]:
# map the start and end locations of the trips on a map and connect them with a line

def map_buffer_zones(dataset):
    
    micromobility_data = check_micromobility_datasets('tier', dataset)
    
    # Create a folium map object
    m = folium.Map(location=[50.73743, 7.09821], zoom_start=12)

    # Iterate over each row in the micromobility data
    for index, row in micromobility_data.iterrows():
        # Get the start and end locations
        start_location = row['start_location']
        end_location = row['end_location']
        
        # Get the start and end stop names
        start_stop_name = row['start_stop_name']
        end_stop_name = row['end_stop_name']
        # Add markers for the start and end locations
        folium.Marker(location=[start_location.y, start_location.x], popup=start_stop_name).add_to(m)
        folium.Marker(location=[end_location.y, end_location.x], popup=end_stop_name).add_to(m)
        # Create a line connecting the start and end locations
        folium.PolyLine(locations=[[start_location.y, start_location.x], [end_location.y, end_location.x]], color='blue').add_to(m)
        
    # Display the map
    return m

In [25]:
def get_stats(data, var):
    
    df = pd.DataFrame()

    for i in var:
        df = pd.concat([df, calc_stats(data, i)], axis=1)

    df.columns = df.iloc[0]
    df = df[1:]
    
    return df

## Create Delay, No_Delay, and Nan-Delay Datasets

In [26]:
delay = data[data['departure_delay'] > pd.Timedelta(0)]


In [27]:
#no_delay = data[data['arrival_delay'] == pd.Timedelta(0)]
#no_delay = data[data['arrival_delay'] == pd.Timedelta(0)]
no_delay = data[
    (data['departure_delay'] == pd.Timedelta(0)) | 
    (data['scheduled_arrival_time'].notna() & 
     data['actual_arrival_time'].isna() & 
     data['scheduled_departure_time'].notna() & 
     data['actual_departure_time'].notna())
]

In [28]:
#nan_delay = data[data['arrival_delay'].isna()]
nan_delay = data[data['scheduled_arrival_time'].notna() & data['actual_arrival_time'].isna() & data['scheduled_departure_time'].notna() & data['actual_departure_time'].isna()]

## Stations

### Buffer Zones of stops

In [29]:
unique_buffer_zones = pd.DataFrame(data['buffer_zone'].unique(), columns=['buffer_zone'])

In [30]:
# Ensure 'geometry' column exists in buffer_gdf
buffer_gdf = gpd.GeoDataFrame(unique_buffer_zones, geometry='buffer_zone')
buffer_gdf['geometry'] = buffer_gdf['buffer_zone']

# Create a folium map
m = folium.Map(location=[buffer_gdf.geometry.centroid.y.mean(), buffer_gdf.geometry.centroid.x.mean()], zoom_start=12)

# Add buffer zones to the map
for _, row in buffer_gdf.iterrows():
    folium.GeoJson(row['geometry']).add_to(m)

# Display the map
m

The map shows all of our PT stations in Bonn. When you compare it the the operating area of the Tier scooters, you see a simmilar image.

### Group by Stations

#### Data

In [31]:
grouped_data = data.groupby('stop_id').agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum'})

In [32]:
merged_data = grouped_data.merge(data[['stop_id', 'station_point', 'stop_name', 'buffer_zone']], on='stop_id', how='left')
merged_data.drop_duplicates(inplace=True)
merged_data

stop_id  tier_trips_count  nextbike_trips_count  \
0             43                56                   123   
3115         161                 0                     6   
4611         371               299                   326   
20965        683                67                   214   
27545        684                89                   259   
...          ...               ...                   ...   
2551510     9716                 0                     2   
2553975     9777                12                     6   
2556962     9778                 1                     1   
2558548     9779                 0                     0   
2560675     9780                 5                    68   

                    station_point                                stop_name  \
0        POINT (7.07351 50.73910)                      Bonn Propsthof Nord   
3115     POINT (7.15955 50.68392)                    Bonn Bad Godesberg Bf   
4611     POINT (7.15835 50.68034)            Bonn Bad Godesberg Stadthalle   
20965    POINT (7.11452 50.72175)                       Bonn Museum Koenig   
27545    POINT (7.11158 50.72556)  Bonn Bundesrechnungshof/Auswärtiges Amt   
...                           ...                                      ...   
2551510  POINT (7.06063 50.73597)              Bonn Gerhart-Hauptmann-Str.   
2553975  POINT (7.04793 50.74116)                         Bonn Kleine Str.   
2556962  POINT (7.07265 50.72710)                      Bonn Magdalenenstr.   
2558548  POINT (7.07273 50.73711)                     Bonn Am Dickobskreuz   
2560675  POINT (7.05240 50.75620)                     Bonn Georg-Elser-Weg   

                                               buffer_zone  
0        POLYGON ((7.07626 50.73943, 7.07630 50.73926, ...  
3115     POLYGON ((7.16230 50.68425, 7.16234 50.68408, ...  
4611     POLYGON ((7.16110 50.68067, 7.16113 50.68050, ...  
20965    POLYGON ((7.11727 50.72208, 7.11731 50.72191, ...  
27545    POLYGON ((7.11433 50.72589, 7.11437 50.72572, ...  
...                                                    ...  
2551510  POLYGON ((7.06338 50.73630, 7.06342 50.73613, ...  
2553975  POLYGON ((7.05068 50.74150, 7.05072 50.74133, ...  
2556962  POLYGON ((7.07540 50.72744, 7.07544 50.72727, ...  
2558548  POLYGON ((7.07548 50.73744, 7.07551 50.73727, ...  
2560675  POLYGON ((7.05515 50.75653, 7.05519 50.75636, ...  

[513 rows x 6 columns]

In [33]:
merged_data_sort_tier = merged_data.sort_values(by='tier_trips_count', ascending=False)
merged_data_sort_tier

stop_id  tier_trips_count  nextbike_trips_count  \
47282        687             15736                 38709   
293126      1115              3005                  7233   
1345567     1500              2893                  4338   
180571      1102              2866                  7129   
274560      1112              1430                  1765   
...          ...               ...                   ...   
1163357     1374                 0                     0   
2307057     7784                 0                     3   
2306587     7729                 0                     1   
1657744     1571                 0                     0   
1814995     1622                 0                     0   

                    station_point                                  stop_name  \
47282    POINT (7.09713 50.73201)                                   Bonn Hbf   
293126   POINT (7.10248 50.73747)  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
1345567  POINT (7.11744 50.73923)                 Bonn Konrad-Adenauer-Platz   
180571   POINT (7.09765 50.73628)                         Bonn Friedensplatz   
274560   POINT (7.10160 50.73909)                           Bonn Stiftsplatz   
...                           ...                                        ...   
1163357  POINT (7.04134 50.69582)                    Bonn Hardthöhe/Südwache   
2307057  POINT (7.15070 50.75124)                    Bonn Gesamtschule Beuel   
2306587  POINT (7.12919 50.71512)                      Bonn Fritz-Erler-Str.   
1657744  POINT (7.20191 50.74461)                         Bonn Kleinfeldstr.   
1814995  POINT (7.15854 50.68708)                           Bonn Königsplatz   

                                               buffer_zone  
47282    POLYGON ((7.09988 50.73234, 7.09992 50.73217, ...  
293126   POLYGON ((7.10523 50.73780, 7.10527 50.73763, ...  
1345567  POLYGON ((7.12019 50.73957, 7.12023 50.73939, ...  
180571   POLYGON ((7.10040 50.73662, 7.10044 50.73644, ...  
274560   POLYGON ((7.10435 50.73943, 7.10439 50.73926, ...  
...                                                    ...  
1163357  POLYGON ((7.04409 50.69616, 7.04412 50.69599, ...  
2307057  POLYGON ((7.15345 50.75158, 7.15349 50.75140, ...  
2306587  POLYGON ((7.13194 50.71546, 7.13198 50.71529, ...  
1657744  POLYGON ((7.20467 50.74494, 7.20470 50.74477, ...  
1814995  POLYGON ((7.16129 50.68741, 7.16133 50.68724, ...  

[513 rows x 6 columns]

In [34]:
t = merged_data_sort_tier.head(20)

In [36]:
t

stop_id  tier_trips_count  nextbike_trips_count  \
47282        687             15736                 38709   
293126      1115              3005                  7233   
1345567     1500              2893                  4338   
180571      1102              2866                  7129   
274560      1112              1430                  1765   
204717      1103              1406                  6682   
2287426     7184               882                  1292   
240068      1106               871                  1830   
2441787     8841               615                  1807   
2212211     2667               599                   731   
40703        686               522                  1002   
1415181     1504               469                   947   
1769844     1604               392                   608   
723172      1240               391                  2107   
625928      1204               363                  2308   
142914       694               330                   935   
384845      1140               313                   717   
470268      1162               307                   777   
1379849     1501               303                   582   
4611         371               299                   326   

                    station_point                                  stop_name  \
47282    POINT (7.09713 50.73201)                                   Bonn Hbf   
293126   POINT (7.10248 50.73747)  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
1345567  POINT (7.11744 50.73923)                 Bonn Konrad-Adenauer-Platz   
180571   POINT (7.09765 50.73628)                         Bonn Friedensplatz   
274560   POINT (7.10160 50.73909)                           Bonn Stiftsplatz   
204717   POINT (7.10263 50.73467)                                 Bonn Markt   
2287426  POINT (7.15804 50.68511)         Bonn Bad Godesberg Bf / Rheinallee   
240068   POINT (7.09487 50.73377)                      Bonn Thomas-Mann-Str.   
2441787  POINT (7.07356 50.72816)                         Bonn Auf Dem Hügel   
2212211  POINT (7.10422 50.73677)  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
40703    POINT (7.10214 50.73234)                     Bonn Universität/Markt   
1415181  POINT (7.12765 50.73848)                              Bonn Beuel Bf   
1769844  POINT (7.15558 50.68328)                            Bonn Am Kurpark   
723172   POINT (7.08848 50.72203)                   Bonn Poppelsdorfer Platz   
625928   POINT (7.08289 50.73250)                              Bonn Karlstr.   
142914   POINT (7.04654 50.75089)                     Bonn Tannenbusch Mitte   
384845   POINT (7.08827 50.73420)                            Bonn Mozartstr.   
470268   POINT (7.09610 50.74188)                              Bonn Rosental   
1379849  POINT (7.12046 50.73937)                         Bonn Beuel Rathaus   
4611     POINT (7.15835 50.68034)              Bonn Bad Godesberg Stadthalle   

                                               buffer_zone  
47282    POLYGON ((7.09988 50.73234, 7.09992 50.73217, ...  
293126   POLYGON ((7.10523 50.73780, 7.10527 50.73763, ...  
1345567  POLYGON ((7.12019 50.73957, 7.12023 50.73939, ...  
180571   POLYGON ((7.10040 50.73662, 7.10044 50.73644, ...  
274560   POLYGON ((7.10435 50.73943, 7.10439 50.73926, ...  
204717   POLYGON ((7.10538 50.73501, 7.10542 50.73483, ...  
2287426  POLYGON ((7.16079 50.68545, 7.16083 50.68527, ...  
240068   POLYGON ((7.09762 50.73411, 7.09766 50.73393, ...  
2441787  POLYGON ((7.07631 50.72850, 7.07634 50.72833, ...  
2212211  POLYGON ((7.10697 50.73710, 7.10701 50.73693, ...  
40703    POLYGON ((7.10489 50.73267, 7.10492 50.73250, ...  
1415181  POLYGON ((7.13040 50.73881, 7.13044 50.73864, ...  
1769844  POLYGON ((7.15832 50.68362, 7.15836 50.68345, ...  
723172   POLYGON ((7.09123 50.72236, 7.09127 50.72219, ...  
625928   POLYGON ((7.08564 50.73284, 7.08568 50.73266, ...  
142914   POLYGON ((7.04929 50.75123, 7.04933 50.75106, ...  
384845   POLYGON ((7.09102 50.

In [39]:
# Ensure 'geometry' column exists in buffer_gdf
buffer_gdf = gpd.GeoDataFrame(t, geometry='buffer_zone')
buffer_gdf['geometry'] = buffer_gdf['buffer_zone']

# Create a folium map
m = folium.Map(location=[buffer_gdf.geometry.centroid.y.mean(), buffer_gdf.geometry.centroid.x.mean()], zoom_start=12)

# Add buffer zones to the map
for _, row in buffer_gdf.iterrows():
    folium.GeoJson(row['geometry']).add_to(m)

# Display the map
m

In [40]:
merged_data_sort_next = merged_data.sort_values(by='nextbike_trips_count', ascending=False)
merged_data_sort_next

stop_id  tier_trips_count  nextbike_trips_count  \
47282        687             15736                 38709   
293126      1115              3005                  7233   
180571      1102              2866                  7129   
204717      1103              1406                  6682   
1345567     1500              2893                  4338   
...          ...               ...                   ...   
759269      1244                22                     0   
2231885     2724                 5                     0   
2207993     2555                 8                     0   
2204350     2553                 0                     0   
1324689     1456                 0                     0   

                    station_point                                  stop_name  \
47282    POINT (7.09713 50.73201)                                   Bonn Hbf   
293126   POINT (7.10248 50.73747)  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
180571   POINT (7.09765 50.73628)                         Bonn Friedensplatz   
204717   POINT (7.10263 50.73467)                                 Bonn Markt   
1345567  POINT (7.11744 50.73923)                 Bonn Konrad-Adenauer-Platz   
...                           ...                                        ...   
759269   POINT (7.08535 50.71095)                         Bonn Am Mühlenberg   
2231885  POINT (7.05437 50.70965)               Bonn Geschwister-Scholl-Str.   
2207993  POINT (7.14566 50.75597)                 Bonn Vilich-Müldorf Kirche   
2204350  POINT (7.19720 50.73745)                      Bonn Friedhof Om Berg   
1324689  POINT (7.04906 50.73593)                      Bonn Dransdorf Kirche   

                                               buffer_zone  
47282    POLYGON ((7.09988 50.73234, 7.09992 50.73217, ...  
293126   POLYGON ((7.10523 50.73780, 7.10527 50.73763, ...  
180571   POLYGON ((7.10040 50.73662, 7.10044 50.73644, ...  
204717   POLYGON ((7.10538 50.73501, 7.10542 50.73483, ...  
1345567  POLYGON ((7.12019 50.73957, 7.12023 50.73939, ...  
...                                                    ...  
759269   POLYGON ((7.08810 50.71128, 7.08814 50.71111, ...  
2231885  POLYGON ((7.05712 50.70999, 7.05716 50.70981, ...  
2207993  POLYGON ((7.14841 50.75630, 7.14845 50.75613, ...  
2204350  POLYGON ((7.19995 50.73778, 7.19999 50.73761, ...  
1324689  POLYGON ((7.05181 50.73627, 7.05185 50.73609, ...  

[513 rows x 6 columns]

In [41]:
t = merged_data_sort_next.head(20)

In [42]:
# Ensure 'geometry' column exists in buffer_gdf
buffer_gdf = gpd.GeoDataFrame(t, geometry='buffer_zone')
buffer_gdf['geometry'] = buffer_gdf['buffer_zone']

# Create a folium map
m = folium.Map(location=[buffer_gdf.geometry.centroid.y.mean(), buffer_gdf.geometry.centroid.x.mean()], zoom_start=12)

# Add buffer zones to the map
for _, row in buffer_gdf.iterrows():
    folium.GeoJson(row['geometry']).add_to(m)

# Display the map
m

Heat Map of all data

In [43]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_data['station_point'], merged_data['tier_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_data['station_point'], merged_data['tier_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [115]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_data['station_point'], merged_data['nextbike_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_data['station_point'], merged_data['nextbike_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

## Delay

In [117]:
delay.columns

Index(['route_id', 'agency_id', 'route_short_name', 'route_type',
       'route_type_name', 'agency_name', 'service_id', 'trip_id',
       'trip_headsign', 'direction_id', 'shape_id', 'stop_id',
       'actual_arrival_time', 'actual_departure_time', 'vrs_timestamp',
       'stop_sequence', 'stop_headsign', 'stop_name', 'scheduled_arrival_time',
       'scheduled_departure_time', 'arrival_delay', 'departure_delay',
       'service', 'date', 'weekday', 'transfer_stop', 'tier_trips_count',
       'tier_trips_id', 'tier_trips_end_at_station_count',
       'tier_trips_end_at_station_id', 'station_point', 'buffer_zone',
       'nextbike_trips_count', 'nextbike_trips_id',
       'nextbike_trips_end_at_station_count',
       'nextbike_trips_end_at_station_id', 'current_time', 'current_temp',
       'current_feels_like', 'current_cloudiness', 'current_visibility',
       'current_wind_speed', 'current_description',
       'current_precipitation_volume', 'arrival_delay_float',
       'departure_

In [118]:
grouped_delay = delay.groupby('stop_id').agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'tier_trips_end_at_station_count' : 'sum', 'nextbike_trips_end_at_station_count': 'sum' ,'departure_delay_float': 'mean'})

In [119]:
merged_delay = grouped_delay.merge(delay[['stop_id', 'station_point', 'stop_name', 'buffer_zone']], on='stop_id', how='left')
merged_delay.drop_duplicates(inplace=True)
merged_delay

stop_id  tier_trips_count  nextbike_trips_count  \
0            43                13                    29   
753         371                 0                     0   
814         683                34                   118   
4391        684                41                   135   
7984        685               103                   926   
...         ...               ...                   ...   
943963     9716                 0                     0   
944987     9777                 5                     4   
946530     9778                 0                     0   
947253     9779                 0                     0   
948160     9780                 4                    31   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
0                                    12                                   26   
753                                   0                                    0   
814                                  30                                   86   
4391                                 30                                  125   
7984                                 88                                  796   
...                                 ...                                  ...   
943963                                0                                    0   
944987                                3                                    2   
946530                                0                                    0   
947253                                0                                    0   
948160                                4                                   23   

        departure_delay_float             station_point  \
0                    0.375830  POINT (7.07351 50.73910)   
753                  6.668033  POINT (7.15835 50.68034)   
814                  0.549949  POINT (7.11452 50.72175)   
4391                 0.549819  POINT (7.11158 50.72556)   
7984                 0.573987  POINT (7.10841 50.73009)   
...                       ...                       ...   
943963               0.514404  POINT (7.06063 50.73597)   
944987               0.554601  POINT (7.04793 50.74116)   
946530               0.549101  POINT (7.07265 50.72710)   
947253               0.473815  POINT (7.07273 50.73711)   
948160               0.397317  POINT (7.05240 50.75620)   

                                      stop_name  \
0                           Bonn Propsthof Nord   
753               Bonn Bad Godesberg Stadthalle   
814                          Bonn Museum Koenig   
4391    Bonn Bundesrechnungshof/Auswärtiges Amt   
7984                             Bonn Juridicum   
...                                         ...   
943963              Bonn Gerhart-Hauptmann-Str.   
944987                         Bonn Kleine Str.   
946530                      Bonn Magdalenenstr.   
947253                     Bonn Am Dickobskreuz   
948160                     Bonn Georg-Elser-Weg   

                                              buffer_zone  
0       POLYGON ((7.07626 50.73943, 7.07630 50.73926, ...  
753     POLYGON ((7.16110 50.68067, 7.16113 50.68050, ...  
814     POLYGON ((7.11727 50.72208, 7.11731 50.72191, ...  
4391    POLYGON ((7.11433 50.72589, 7.11437 50.72572, ...  
7984    POLYGON ((7.11116 50.73043, 7.11120 50.73026, ...  
...                                                   ...  
943963  POLYGON ((7.06338 50.73630, 7.06342 50.73613, ...  
944987  POLYGON ((7.05068 50.74150, 7.05072 50.74133, ...  
946530  POLYGON ((7.07540 50.72744, 7.07544 50.72727, ...  
947253  POLYGON ((7.07548 50.73744, 7.07551 50.73727, ...  
948160  POLYGON ((7.05515 50.75653, 7.05519 50.75636, ...  

[479 rows x 9 columns]

In [50]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_delay['station_point'], merged_delay['tier_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_delay['station_point'], merged_delay['tier_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [120]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_delay['station_point'], merged_delay['tier_trips_end_at_station_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_delay['station_point'], merged_delay['tier_trips_end_at_station_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [121]:
merged_delay_sort_tier = merged_delay.sort_values(by='tier_trips_count', ascending=False).head(50)
merged_delay_sort_tier

stop_id  tier_trips_count  nextbike_trips_count  \
34661      1102              1485                  3984   
76641      1112               680                   817   
85916      1115               625                  1215   
47204      1103               594                  3288   
13198       687               588                   997   
60417      1106               432                   871   
903521     8841               274                   758   
513455     1500               238                   452   
264724     1240               211                  1161   
217761     1204               190                  1232   
651610     1604               176                   238   
689822     1650               156                   153   
249777     1224               146                   753   
517683     1501               140                   268   
868254     8507               139                   188   
525824     1502               127                   303   
23147       694               108                   322   
145978     1160               107                   278   
132542     1145               104                   202   
181529     1182               103                   221   
7984        685               103                   926   
70861      1110               103                   339   
244278     1223               102                   998   
115106     1140                98                   233   
151547     1162                97                   249   
941216     9712                94                   276   
209621     1203                90                   393   
96869      1123                85                   143   
661466     1620                83                   476   
17601       692                73                   223   
11613       686                70                   221   
295299     1261                67                   188   
55772      1104                66                   164   
534009     1504                62                   117   
818039     2667                57                    90   
127015     1144                56                   208   
143432     1153                55                   217   
255887     1231                54                   106   
148440     1161                50                   268   
765268     1762                49                   223   
241154     1221                48                   637   
154415     1171                48                    51   
107233     1131                47                   254   
166291     1176                46                    55   
14729       691                44                    74   
111371     1135                44                    83   
681260     1640                44                    43   
705025     1670                43                    45   
399456     1342                43                    15   
298674     1263                42                   152   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
34661                              1240                                 3448   
76641                               577                                  676   
85916                               513                                  998   
47204                               432                                 2733   
13198                               499                                  846   
60417                               381                                  770   
903521                              248                                  661   
513455                              172                                  343   
264724                              190                                 1014   
217761                              152                                 1095   
651610                              139                                  164   
689822                              11

In [122]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_delay_sort_tier['station_point'], merged_delay_sort_tier['tier_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_delay_sort_tier['station_point'], merged_delay_sort_tier['tier_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [123]:
merged_delay_sort_next = merged_delay.sort_values(by='nextbike_trips_count', ascending=False).head(50)
merged_delay_sort_next

stop_id  tier_trips_count  nextbike_trips_count  \
34661      1102              1485                  3984   
47204      1103               594                  3288   
217761     1204               190                  1232   
85916      1115               625                  1215   
264724     1240               211                  1161   
244278     1223               102                   998   
13198       687               588                   997   
7984        685               103                   926   
60417      1106               432                   871   
76641      1112               680                   817   
903521     8841               274                   758   
249777     1224               146                   753   
241154     1221                48                   637   
661466     1620                83                   476   
513455     1500               238                   452   
209621     1203                90                   393   
70861      1110               103                   339   
23147       694               108                   322   
525824     1502               127                   303   
145978     1160               107                   278   
941216     9712                94                   276   
517683     1501               140                   268   
148440     1161                50                   268   
107233     1131                47                   254   
151547     1162                97                   249   
204634     1202                13                   239   
651610     1604               176                   238   
115106     1140                98                   233   
163644     1174                29                   224   
765268     1762                49                   223   
17601       692                73                   223   
181529     1182               103                   221   
11613       686                70                   221   
143432     1153                55                   217   
127015     1144                56                   208   
132542     1145               104                   202   
295299     1261                67                   188   
868254     8507               139                   188   
158023     1172                37                   179   
237237     1214                41                   173   
850067     8437                24                   173   
55772      1104                66                   164   
231083     1212                42                   157   
198265     1194                21                   154   
689822     1650               156                   153   
298674     1263                42                   152   
96869      1123                85                   143   
924963     9081                20                   140   
124323     1143                34                   140   
196513     1192                26                   140   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
34661                              1240                                 3448   
47204                               432                                 2733   
217761                              152                                 1095   
85916                               513                                  998   
264724                              190                                 1014   
244278                               88                                  886   
13198                               499                                  846   
7984                                 88                                  796   
60417                               381                                  770   
76641                               577                                  676   
903521                              248                                  661   
249777                              12

In [162]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_delay_sort_next['station_point'], merged_delay_sort_next['nextbike_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_delay_sort_next['station_point'], merged_delay_sort_next['nextbike_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [ ]:
#tier_trips_end_at_station_count

In [126]:
merged_delay_sort_tier_end = merged_delay.sort_values(by='tier_trips_end_at_station_count', ascending=False).head(50)
merged_delay_sort_tier_end

stop_id  tier_trips_count  nextbike_trips_count  \
34661      1102              1485                  3984   
76641      1112               680                   817   
85916      1115               625                  1215   
13198       687               588                   997   
47204      1103               594                  3288   
60417      1106               432                   871   
903521     8841               274                   758   
264724     1240               211                  1161   
513455     1500               238                   452   
217761     1204               190                  1232   
651610     1604               176                   238   
249777     1224               146                   753   
689822     1650               156                   153   
868254     8507               139                   188   
517683     1501               140                   268   
525824     1502               127                   303   
145978     1160               107                   278   
23147       694               108                   322   
132542     1145               104                   202   
70861      1110               103                   339   
244278     1223               102                   998   
7984        685               103                   926   
151547     1162                97                   249   
115106     1140                98                   233   
209621     1203                90                   393   
181529     1182               103                   221   
96869      1123                85                   143   
661466     1620                83                   476   
941216     9712                94                   276   
55772      1104                66                   164   
11613       686                70                   221   
17601       692                73                   223   
295299     1261                67                   188   
127015     1144                56                   208   
255887     1231                54                   106   
818039     2667                57                    90   
143432     1153                55                   217   
534009     1504                62                   117   
154415     1171                48                    51   
166291     1176                46                    55   
241154     1221                48                   637   
107233     1131                47                   254   
224813     1210                41                   109   
148440     1161                50                   268   
231083     1212                42                   157   
111371     1135                44                    83   
454943     1406                40                   120   
237237     1214                41                   173   
399456     1342                43                    15   
681260     1640                44                    43   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
34661                              1240                                 3448   
76641                               577                                  676   
85916                               513                                  998   
13198                               499                                  846   
47204                               432                                 2733   
60417                               381                                  770   
903521                              248                                  661   
264724                              190                                 1014   
513455                              172                                  343   
217761                              152                                 1095   
651610                              139                                  164   
249777                              12

In [127]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_delay_sort_tier_end['station_point'], merged_delay_sort_tier_end['tier_trips_end_at_station_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_delay_sort_tier_end['station_point'], merged_delay_sort_tier_end['tier_trips_end_at_station_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [129]:
merged_delay_sort_next_end = merged_delay.sort_values(by='nextbike_trips_end_at_station_count', ascending=False).head(50)
merged_delay_sort_next_end

stop_id  tier_trips_count  nextbike_trips_count  \
34661      1102              1485                  3984   
47204      1103               594                  3288   
217761     1204               190                  1232   
264724     1240               211                  1161   
85916      1115               625                  1215   
244278     1223               102                   998   
13198       687               588                   997   
7984        685               103                   926   
60417      1106               432                   871   
249777     1224               146                   753   
76641      1112               680                   817   
903521     8841               274                   758   
241154     1221                48                   637   
661466     1620                83                   476   
209621     1203                90                   393   
513455     1500               238                   452   
70861      1110               103                   339   
23147       694               108                   322   
145978     1160               107                   278   
525824     1502               127                   303   
204634     1202                13                   239   
107233     1131                47                   254   
148440     1161                50                   268   
941216     9712                94                   276   
151547     1162                97                   249   
115106     1140                98                   233   
143432     1153                55                   217   
517683     1501               140                   268   
132542     1145               104                   202   
181529     1182               103                   221   
163644     1174                29                   224   
127015     1144                56                   208   
11613       686                70                   221   
17601       692                73                   223   
651610     1604               176                   238   
868254     8507               139                   188   
237237     1214                41                   173   
850067     8437                24                   173   
55772      1104                66                   164   
158023     1172                37                   179   
295299     1261                67                   188   
198265     1194                21                   154   
231083     1212                42                   157   
689822     1650               156                   153   
4391        684                41                   135   
196513     1192                26                   140   
290867     1255                36                   139   
924963     9081                20                   140   
96869      1123                85                   143   
124323     1143                34                   140   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
34661                              1240                                 3448   
47204                               432                                 2733   
217761                              152                                 1095   
264724                              190                                 1014   
85916                               513                                  998   
244278                               88                                  886   
13198                               499                                  846   
7984                                 88                                  796   
60417                               381                                  770   
249777                              125                                  685   
76641                               577                                  676   
903521                              24

In [130]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_delay_sort_next_end['station_point'], merged_delay_sort_next_end['nextbike_trips_end_at_station_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_delay_sort_next_end['station_point'], merged_delay_sort_next_end['nextbike_trips_end_at_station_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [131]:
merged_delay_sort_delay = merged_delay.sort_values(by='departure_delay_float', ascending=False).head(50)
merged_delay_sort_delay

stop_id  tier_trips_count  nextbike_trips_count  \
107217     1130                 0                     0   
307155     1270                 0                     0   
14583       690                 0                     0   
308480     1273                 0                     0   
29450       698                 3                     1   
710722     1681                 1                     0   
713052     1683                 3                     3   
715801     1687                 1                     0   
713945     1684                 0                     0   
324296     1293                 0                     0   
29615       699                 6                     8   
109007     1132                 0                     0   
753         371                 0                     0   
711783     1682                10                     0   
880097     8629                 6                     3   
313649     1286                 0                     1   
625764     1584                 2                     0   
816282     2576                 5                    18   
621008     1580                 2                     1   
17601       692                73                   223   
184668     1183                27                    67   
931810     9478                 0                     2   
928671     9477                32                   131   
309115     1280                 2                     3   
883310     8634                 6                     5   
933862     9703                 8                     6   
587237     1551                 0                     0   
777943     2312                 0                     1   
127015     1144                56                   208   
707756     1671                17                    11   
132542     1145               104                   202   
99483      1124                39                   109   
669749     1625                 8                    26   
96869      1123                85                   143   
651610     1604               176                   238   
585363     1550                12                    11   
719007     1711                19                    15   
509165     1459                20                   100   
399350     1341                 0                     2   
454943     1406                40                   120   
55772      1104                66                   164   
217761     1204               190                  1232   
111371     1135                44                    83   
828714     2749                 1                     6   
338008     1303                 4                     1   
14729       691                44                    74   
778502     2313                 2                     2   
621316     1581                13                     7   
613258     1568                18                     5   
578702     1542                 8                     9   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
107217                                0                                    0   
307155                                0                                    0   
14583                                 0                                    0   
308480                                0                                    0   
29450                                 3                                    0   
710722                                1                                    0   
713052                                2                                    1   
715801                                1                                    0   
713945                                0                                    0   
324296                                0                                    0   
29615                                 5                                    7   
109007                                

In [132]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_delay_sort_delay['station_point'], merged_delay_sort_delay['departure_delay_float'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_delay_sort_delay['station_point'], merged_delay_sort_delay['departure_delay_float']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

## No Delay

In [140]:
grouped_no_delay = no_delay.groupby('stop_id').agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'tier_trips_end_at_station_count': 'sum', 'nextbike_trips_end_at_station_count': 'sum', 'departure_delay_float': 'mean'})
grouped_no_delay = grouped_no_delay.merge(no_delay[['stop_id', 'station_point', 'stop_name', 'buffer_zone']], on='stop_id', how='left')
grouped_no_delay.drop_duplicates(inplace=True)
grouped_no_delay

stop_id  tier_trips_count  nextbike_trips_count  \
0            43                22                    45   
1112        161                 0                     4   
2080        371               170                   203   
12346       683                 2                     5   
12559       684                 4                     5   
...         ...               ...                   ...   
598536     9716                 0                     1   
598947     9777                 0                     1   
599077     9778                 0                     0   
599424     9779                 0                     0   
599554     9780                 1                    12   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
0                                    22                                   40   
1112                                  0                                    3   
2080                                128                                  174   
12346                                 1                                    5   
12559                                 4                                    4   
...                                 ...                                  ...   
598536                                0                                    1   
598947                                0                                    1   
599077                                0                                    0   
599424                                0                                    0   
599554                                1                                   10   

        departure_delay_float             station_point  \
0                    0.005845  POINT (7.07351 50.73910)   
1112                 0.000000  POINT (7.15955 50.68392)   
2080                 0.000000  POINT (7.15835 50.68034)   
12346                0.137715  POINT (7.11452 50.72175)   
12559                0.133020  POINT (7.11158 50.72556)   
...                       ...                       ...   
598536               0.032238  POINT (7.06063 50.73597)   
598947               0.144231  POINT (7.04793 50.74116)   
599077               0.020893  POINT (7.07265 50.72710)   
599424               0.015385  POINT (7.07273 50.73711)   
599554               0.005208  POINT (7.05240 50.75620)   

                                      stop_name  \
0                           Bonn Propsthof Nord   
1112                      Bonn Bad Godesberg Bf   
2080              Bonn Bad Godesberg Stadthalle   
12346                        Bonn Museum Koenig   
12559   Bonn Bundesrechnungshof/Auswärtiges Amt   
...                                         ...   
598536              Bonn Gerhart-Hauptmann-Str.   
598947                         Bonn Kleine Str.   
599077                      Bonn Magdalenenstr.   
599424                     Bonn Am Dickobskreuz   
599554                     Bonn Georg-Elser-Weg   

                                              buffer_zone  
0       POLYGON ((7.07626 50.73943, 7.07630 50.73926, ...  
1112    POLYGON ((7.16230 50.68425, 7.16234 50.68408, ...  
2080    POLYGON ((7.16110 50.68067, 7.16113 50.68050, ...  
12346   POLYGON ((7.11727 50.72208, 7.11731 50.72191, ...  
12559   POLYGON ((7.11433 50.72589, 7.11437 50.72572, ...  
...                                                   ...  
598536  POLYGON ((7.06338 50.73630, 7.06342 50.73613, ...  
598947  POLYGON ((7.05068 50.74150, 7.05072 50.74133, ...  
599077  POLYGON ((7.07540 50.72744, 7.07544 50.72727, ...  
599424  POLYGON ((7.07548 50.73744, 7.07551 50.73727, ...  
599554  POLYGON ((7.05515 50.75653, 7.05519 50.75636, ...  

[508 rows x 9 columns]

In [59]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_no_delay['station_point'], grouped_no_delay['tier_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_no_delay['station_point'], grouped_no_delay['tier_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [133]:
grouped_no_delay_sort_tier = grouped_no_delay.sort_values(by='tier_trips_count', ascending=False).head(50)
grouped_no_delay_sort_tier

stop_id  tier_trips_count  nextbike_trips_count  \
15271       687              8917                 21042   
316932     1500              1508                  2151   
93053      1115              1139                  2973   
540617     7184               500                   680   
72690      1102               361                   656   
518250     2667               283                   336   
76020      1103               269                   799   
90527      1112               229                   283   
13034       686               217                   331   
338399     1504               216                   413   
2080        371               170                   203   
402117     1584               134                   246   
257168     1344               130                    71   
84565      1106               126                   354   
241202     1341               124                    38   
571912     8841               111                   442   
120400     1140               104                   239   
66710       699               101                   164   
61878       694                96                   251   
80700      1104                85                   137   
55452       692                82                   247   
139651     1162                82                   193   
157566     1182                77                   183   
420548     1604                73                   162   
583711     9477                67                   276   
171960     1204                67                   345   
487716     1762                67                   191   
134250     1151                66                   447   
48235       688                64                   143   
177940     1221                61                  1412   
251557     1342                56                    13   
111745     1123                55                   101   
160224     1184                53                   176   
295280     1406                47                   109   
144187     1175                47                   235   
113435     1124                46                   215   
137983     1160                44                   167   
124553     1141                42                   159   
424650     1607                42                    67   
336206     1502                38                    64   
357418     1522                34                    31   
412505     1593                33                    40   
558931     8578                32                    59   
198681     1280                31                    42   
333919     1501                30                    72   
476415     1742                27                    36   
136825     1153                26                   190   
87389      1110                26                    23   
391736     1568                26                     7   
354883     1521                26                    31   

                   station_point                                  stop_name  \
15271   POINT (7.09713 50.73201)                                   Bonn Hbf   
316932  POINT (7.11744 50.73923)                 Bonn Konrad-Adenauer-Platz   
93053   POINT (7.10248 50.73747)  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
540617  POINT (7.15804 50.68511)         Bonn Bad Godesberg Bf / Rheinallee   
72690   POINT (7.09765 50.73628)                         Bonn Friedensplatz   
518250  POINT (7.10422 50.73677)  Bonn Brüdergasse/Bertha-Von-Suttner-Platz   
76020   POINT (7.10263 50.73467)                                 Bonn Markt   
90527   POINT (7.10160 50.73909)                           Bonn Stiftsplatz   
13034   POINT (7.10214 50.73234)                     Bonn Universität/Markt   
338399  POINT (7.12765 50.73848)                              Bonn Beuel Bf   
2080    POINT (7.15835 50.68034)              Bonn Bad Godesberg Stadthalle   
402117  POINT (7.15513 50.72238)                  

In [134]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_no_delay_sort_tier['station_point'], grouped_no_delay_sort_tier['tier_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_no_delay_sort_tier['station_point'], grouped_no_delay_sort_tier['tier_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [135]:
grouped_no_delay_sort_next = grouped_no_delay.sort_values(by='nextbike_trips_count', ascending=False).head(50)
grouped_no_delay_sort_next

stop_id  tier_trips_count  nextbike_trips_count  \
15271       687              8917                 21042   
93053      1115              1139                  2973   
316932     1500              1508                  2151   
177940     1221                61                  1412   
76020      1103               269                   799   
540617     7184               500                   680   
72690      1102               361                   656   
134250     1151                66                   447   
571912     8841               111                   442   
338399     1504               216                   413   
84565      1106               126                   354   
171960     1204                67                   345   
518250     2667               283                   336   
13034       686               217                   331   
90527      1112               229                   283   
583711     9477                67                   276   
61878       694                96                   251   
55452       692                82                   247   
402117     1584               134                   246   
120400     1140               104                   239   
144187     1175                47                   235   
113435     1124                46                   215   
2080        371               170                   203   
139651     1162                82                   193   
487716     1762                67                   191   
182957     1224                24                   190   
136825     1153                26                   190   
157566     1182                77                   183   
160224     1184                53                   176   
137983     1160                44                   167   
66710       699               101                   164   
420548     1604                73                   162   
124553     1141                42                   159   
132073     1145                23                   154   
48235       688                64                   143   
80700      1104                85                   137   
186507     1240                21                   128   
295280     1406                47                   109   
111745     1123                55                   101   
182190     1223                17                    91   
143112     1174                10                    90   
430269     1620                14                    88   
200583     1286                 5                    73   
333919     1501                30                    72   
257168     1344               130                    71   
133257     1150                22                    68   
424650     1607                42                    67   
336206     1502                38                    64   
492819     1950                16                    62   
149689     1177                12                    60   

                   station_point                                  stop_name  \
15271   POINT (7.09713 50.73201)                                   Bonn Hbf   
93053   POINT (7.10248 50.73747)  Bonn Bertha-Von-Suttner-Pl./Beethovenhaus   
316932  POINT (7.11744 50.73923)                 Bonn Konrad-Adenauer-Platz   
177940  POINT (7.08446 50.72827)                          Bonn Kaufmannstr.   
76020   POINT (7.10263 50.73467)                                 Bonn Markt   
540617  POINT (7.15804 50.68511)         Bonn Bad Godesberg Bf / Rheinallee   
72690   POINT (7.09765 50.73628)                         Bonn Friedensplatz   
134250  POINT (7.08766 50.73971)                Bonn Frankenbad/Kunstverein   
571912  POINT (7.07356 50.72816)                         Bonn Auf Dem Hügel   
338399  POINT (7.12765 50.73848)                              Bonn Beuel Bf   
84565   POINT (7.09487 50.73377)                      Bonn Thomas-Mann-Str.   
171960  POINT (7.08289 50.73250)                  

In [137]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_no_delay_sort_next['station_point'], grouped_no_delay_sort_next['nextbike_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_no_delay_sort_next['station_point'], grouped_no_delay_sort_next['nextbike_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [141]:
grouped_no_delay_sort_next_end = grouped_no_delay.sort_values(by='nextbike_trips_end_at_station_count', ascending=False).head(50)
grouped_no_delay_sort_next_end

stop_id  tier_trips_count  nextbike_trips_count  \
15271       687              8917                 21042   
93053      1115              1139                  2973   
316932     1500              1508                  2151   
177940     1221                61                  1412   
76020      1103               269                   799   
72690      1102               361                   656   
540617     7184               500                   680   
571912     8841               111                   442   
134250     1151                66                   447   
338399     1504               216                   413   
171960     1204                67                   345   
84565      1106               126                   354   
13034       686               217                   331   
518250     2667               283                   336   
90527      1112               229                   283   
120400     1140               104                   239   
55452       692                82                   247   
583711     9477                67                   276   
61878       694                96                   251   
144187     1175                47                   235   
113435     1124                46                   215   
2080        371               170                   203   
182957     1224                24                   190   
136825     1153                26                   190   
139651     1162                82                   193   
157566     1182                77                   183   
132073     1145                23                   154   
124553     1141                42                   159   
137983     1160                44                   167   
160224     1184                53                   176   
402117     1584               134                   246   
66710       699               101                   164   
80700      1104                85                   137   
420548     1604                73                   162   
186507     1240                21                   128   
48235       688                64                   143   
295280     1406                47                   109   
111745     1123                55                   101   
182190     1223                17                    91   
487716     1762                67                   191   
430269     1620                14                    88   
143112     1174                10                    90   
257168     1344               130                    71   
133257     1150                22                    68   
200583     1286                 5                    73   
424650     1607                42                    67   
117437     1133                14                    57   
336206     1502                38                    64   
333919     1501                30                    72   
149689     1177                12                    60   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
15271                              7431                                18076   
93053                               898                                 2433   
316932                             1085                                 1621   
177940                               51                                 1294   
76020                               200                                  663   
72690                               308                                  560   
540617                              379                                  469   
571912                              102                                  395   
134250                               61                                  386   
338399                              170                                  335   
171960                               57                                  310   
84565                               11

In [143]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_no_delay_sort_next_end ['station_point'], grouped_no_delay_sort_next_end ['nextbike_trips_end_at_station_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_no_delay_sort_next_end ['station_point'], grouped_no_delay_sort_next_end ['nextbike_trips_end_at_station_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [142]:
grouped_no_delay_sort_tier_end = grouped_no_delay.sort_values(by='tier_trips_end_at_station_count', ascending=False).head(50)
grouped_no_delay_sort_tier_end

stop_id  tier_trips_count  nextbike_trips_count  \
15271       687              8917                 21042   
316932     1500              1508                  2151   
93053      1115              1139                  2973   
540617     7184               500                   680   
72690      1102               361                   656   
518250     2667               283                   336   
76020      1103               269                   799   
90527      1112               229                   283   
13034       686               217                   331   
338399     1504               216                   413   
2080        371               170                   203   
84565      1106               126                   354   
571912     8841               111                   442   
120400     1140               104                   239   
257168     1344               130                    71   
61878       694                96                   251   
402117     1584               134                   246   
80700      1104                85                   137   
66710       699               101                   164   
241202     1341               124                    38   
139651     1162                82                   193   
55452       692                82                   247   
157566     1182                77                   183   
134250     1151                66                   447   
420548     1604                73                   162   
171960     1204                67                   345   
48235       688                64                   143   
251557     1342                56                    13   
177940     1221                61                  1412   
160224     1184                53                   176   
583711     9477                67                   276   
111745     1123                55                   101   
295280     1406                47                   109   
137983     1160                44                   167   
144187     1175                47                   235   
113435     1124                46                   215   
124553     1141                42                   159   
424650     1607                42                    67   
487716     1762                67                   191   
336206     1502                38                    64   
412505     1593                33                    40   
87389      1110                26                    23   
182957     1224                24                   190   
136825     1153                26                   190   
198681     1280                31                    42   
132073     1145                23                   154   
558931     8578                32                    59   
0            43                22                    45   
391736     1568                26                     7   
333919     1501                30                    72   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
15271                              7431                                18076   
316932                             1085                                 1621   
93053                               898                                 2433   
540617                              379                                  469   
72690                               308                                  560   
518250                              221                                  251   
76020                               200                                  663   
90527                               190                                  230   
13034                               182                                  277   
338399                              170                                  335   
2080                                128                                  174   
84565                               11

In [145]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_no_delay_sort_tier_end ['station_point'], grouped_no_delay_sort_tier_end ['tier_trips_end_at_station_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_no_delay_sort_tier_end ['station_point'], grouped_no_delay_sort_tier_end ['tier_trips_end_at_station_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [146]:
grouped_no_delay_sort_delay= grouped_no_delay.sort_values(by='departure_delay_float', ascending=False).head(50)
grouped_no_delay_sort_delay

stop_id  tier_trips_count  nextbike_trips_count  \
442990     1684                 0                     0   
442846     1683                 0                     0   
160017     1183                 2                     5   
562051     8629                 1                     0   
518212     2576                 0                     0   
532602     5568                 0                     3   
165099     1192                 2                     1   
132073     1145                23                   154   
130961     1144                18                    37   
283528     1381                 6                     0   
291722     1400                 0                     0   
492632     1766                 0                     0   
467960     1737                 0                     0   
555449     8087                 0                     0   
439236     1665                 0                     0   
595865     9705                 1                     1   
163140     1185                 0                     0   
369154     1544                 0                     0   
282112     1375                 0                     0   
441285     1681                 1                     0   
268816     1350                 0                     0   
299309     1409                 0                     0   
435020     1643                 2                     0   
438460     1663                 0                     0   
554793     8006                 0                     0   
373999     1551                 0                     0   
594290     9703                 2                     5   
442182     1682                13                     0   
444076     1687                 1                     0   
508945     2519                 0                     0   
557912     8471                 0                     0   
307631     1445                 0                     0   
431415     1622                 0                     0   
300032     1413                 0                     0   
431435     1625                 3                     3   
118927     1135                14                    19   
435824     1653                 0                     0   
195131     1260                 1                     1   
269782     1353                 0                     0   
221469     1314                 0                     0   
507334     2514                 0                     0   
368704     1542                 0                     0   
305764     1441                 0                     0   
557986     8506                 0                     1   
133219     1146                 0                     0   
576238     8950                 0                     6   
302074     1430                 0                     0   
440641     1673                 0                     0   
435805     1651                 0                     0   
130831     1143                 1                     5   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
442990                                0                                    0   
442846                                0                                    0   
160017                                1                                    5   
562051                                1                                    0   
518212                                0                                    0   
532602                                0                                    2   
165099                                2                                    1   
132073                               23                                  147   
130961                               18                                   30   
283528                                5                                    0   
291722                                0                                    0   
492632                                

In [147]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_no_delay_sort_delay['station_point'], grouped_no_delay_sort_delay['departure_delay_float'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_no_delay_sort_delay['station_point'], grouped_no_delay_sort_delay['departure_delay_float']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

## Nan Delay

In [156]:
grouped_nan_delay = nan_delay.groupby('stop_id').agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'cancelled_trip': 'sum', 'tier_trips_end_at_station_count': 'sum', 'nextbike_trips_end_at_station_count': 'sum'})
grouped_nan_delay = grouped_nan_delay.merge(nan_delay[['stop_id', 'station_point', 'stop_name', 'buffer_zone']], on='stop_id', how='left')
grouped_nan_delay.drop_duplicates(inplace=True)
grouped_nan_delay

stop_id  tier_trips_count  nextbike_trips_count  cancelled_trip  \
0             43                21                    51            1265   
1265         161                 0                     2             528   
1793         371               115                   117            5615   
7408         683                32                    94            2841   
10249        684                45                   120            2827   
...          ...               ...                   ...             ...   
1000117     9716                 0                     1            1061   
1001178     9777                 7                     1            1349   
1002527     9778                 1                     1             528   
1003055     9779                 0                     0            1095   
1004150     9780                 0                    25            1463   

         tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
0                                     19                                   48   
1265                                   0                                    2   
1793                                  88                                  102   
7408                                  23                                   81   
10249                                 35                                  105   
...                                  ...                                  ...   
1000117                                0                                    1   
1001178                                6                                    1   
1002527                                1                                    1   
1003055                                0                                    0   
1004150                                0                                   17   

                    station_point                                stop_name  \
0        POINT (7.07351 50.73910)                      Bonn Propsthof Nord   
1265     POINT (7.15955 50.68392)                    Bonn Bad Godesberg Bf   
1793     POINT (7.15835 50.68034)            Bonn Bad Godesberg Stadthalle   
7408     POINT (7.11452 50.72175)                       Bonn Museum Koenig   
10249    POINT (7.11158 50.72556)  Bonn Bundesrechnungshof/Auswärtiges Amt   
...                           ...                                      ...   
1000117  POINT (7.06063 50.73597)              Bonn Gerhart-Hauptmann-Str.   
1001178  POINT (7.04793 50.74116)                         Bonn Kleine Str.   
1002527  POINT (7.07265 50.72710)                      Bonn Magdalenenstr.   
1003055  POINT (7.07273 50.73711)                     Bonn Am Dickobskreuz   
1004150  POINT (7.05240 50.75620)                     Bonn Georg-Elser-Weg   

                                               buffer_zone  
0        POLYGON ((7.07626 50.73943, 7.07630 50.73926, ...  
1265     POLYGON ((7.16230 50.68425, 7.16234 50.68408, ...  
1793     POLYGON ((7.16110 50.68067, 7.16113 50.68050, ...  
7408     POLYGON ((7.11727 50.72208, 7.11731 50.72191, ...  
10249    POLYGON ((7.11433 50.72589, 7.11437 50.72572, ...  
...                                                    ...  
1000117  POLYGON ((7.06338 50.73630, 7.06342 50.73613, ...  
1001178  POLYGON ((7.05068 50.74150, 7.05072 50.74133, ...  
1002527  POLYGON ((7.07540 50.72744, 7.07544 50.72727, ...  
1003055  POLYGON ((7.07548 50.73744, 7.07551 50.73727, ...  
1004150  POLYGON ((7.05515 50.75653, 7.05519 50.75636, ...  

[513 rows x 9 columns]

In [67]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_nan_delay['station_point'], grouped_nan_delay['tier_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_nan_delay['station_point'], grouped_nan_delay['tier_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [148]:
grouped_nan_delay_sort_tier = grouped_nan_delay.sort_values(by='tier_trips_count', ascending=False).head(50)
grouped_nan_delay_sort_tier

stop_id  tier_trips_count  nextbike_trips_count  cancelled_trip  \
18633       687              5297                 14357           20974   
111121     1115              1202                  2964           17453   
508228     1500              1167                  1760           13401   
68705      1102              1052                  2568            8632   
77337      1103               574                  2699            7986   
104034     1112               550                   703            4724   
91077      1106               321                   620            6914   
899689     7184               299                   456            4480   
868721     2667               262                   309            6988   
15866       686               235                   448            2767   
958796     8841               231                   618            6127   
536632     1504               192                   428            4478   
272756     1240               162                   851            5653   
692619     1604               150                   221            4339   
521629     1501               138                   260            7485   
177170     1162               134                   371            3343   
660841     1584               127                   229            7749   
53342       694               126                   348            4499   
46785       692               118                   273            5042   
1793        371               115                   117            5615   
235853     1204               114                   786            4807   
529114     1502               114                   246            4833   
146237     1140               112                   246            4102   
260324     1224               110                   627            4122   
206396     1182               107                   280            3730   
85323      1104               105                   281            5754   
172717     1160                94                   264            2225   
394767     1341                92                    20            6408   
729773     1650                91                    88            2965   
97991      1110                90                   280            3388   
407114     1344                87                    45            4027   
60736       699                86                   166            2418   
160947     1145                84                   193            3852   
813302     1762                84                   279            4427   
168169     1151                83                   361            2126   
252379     1221                80                  1528            4501   
13076       685                78                   845            2790   
459802     1406                74                   142            5415   
979231     9477                73                   325            5452   
928102     8507                71                   103            3023   
704357     1620                61                   341            4525   
264446     1231                53                    79            3363   
256880     1223                51                   652            3444   
212461     1184                48                   110            2724   
401175     1342                48                    16            5939   
174942     1161                48                   178            2228   
321118     1291                46                     7            3613   
232355     1203                46                   159            3498   
10249       684                45                   120            2827   
884323     2802                44                    55            3695   

                   station_point                                  stop_name  \
18633   POINT (7.09713 50.73201)                                   Bonn Hbf   
111121  POINT (7.10248 5

In [149]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_nan_delay_sort_tier['station_point'], grouped_nan_delay_sort_tier['tier_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_nan_delay_sort_tier['station_point'], grouped_nan_delay_sort_tier['tier_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [150]:
grouped_nan_delay_sort_next = grouped_nan_delay.sort_values(by='nextbike_trips_count', ascending=False).head(50)
grouped_nan_delay_sort_next

stop_id  tier_trips_count  nextbike_trips_count  cancelled_trip  \
18633       687              5297                 14357           20974   
111121     1115              1202                  2964           17453   
77337      1103               574                  2699            7986   
68705      1102              1052                  2568            8632   
508228     1500              1167                  1760           13401   
252379     1221                80                  1528            4501   
272756     1240               162                   851            5653   
13076       685                78                   845            2790   
235853     1204               114                   786            4807   
104034     1112               550                   703            4724   
256880     1223                51                   652            3444   
260324     1224               110                   627            4122   
91077      1106               321                   620            6914   
958796     8841               231                   618            6127   
899689     7184               299                   456            4480   
15866       686               235                   448            2767   
536632     1504               192                   428            4478   
177170     1162               134                   371            3343   
168169     1151                83                   361            2126   
53342       694               126                   348            4499   
704357     1620                61                   341            4525   
979231     9477                73                   325            5452   
868721     2667               262                   309            6988   
85323      1104               105                   281            5754   
206396     1182               107                   280            3730   
97991      1110                90                   280            3388   
813302     1762                84                   279            4427   
46785       692               118                   273            5042   
172717     1160                94                   264            2225   
521629     1501               138                   260            7485   
529114     1502               114                   246            4833   
146237     1140               112                   246            4102   
170326     1153                42                   238            2391   
660841     1584               127                   229            7749   
692619     1604               150                   221            4339   
160947     1145                84                   193            3852   
187067     1174                22                   185            2170   
174942     1161                48                   178            2228   
228964     1202                23                   178            3391   
189237     1175                33                   176            2913   
60736       699                86                   166            2418   
232355     1203                46                   159            3498   
138240     1131                35                   152            1261   
998079     9712                40                   145            1155   
974281     9069                 6                   144             700   
459802     1406                74                   142            5415   
182703     1172                16                   141            2190   
295853     1255                33                   128            2201   
299581     1261                31                   127            2247   
157649     1144                34                   123            3298   

                   station_point                                  stop_name  \
18633   POINT (7.09713 50.73201)                                   Bonn Hbf   
111121  POINT (7.10248 5

In [151]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_nan_delay_sort_next['station_point'], grouped_nan_delay_sort_next['nextbike_trips_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_nan_delay_sort_next['station_point'], grouped_nan_delay_sort_next['nextbike_trips_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [157]:
grouped_nan_delay_sort_next_end = grouped_nan_delay.sort_values(by='nextbike_trips_end_at_station_count', ascending=False).head(50)
grouped_nan_delay_sort_next_end

stop_id  tier_trips_count  nextbike_trips_count  cancelled_trip  \
18633       687              5297                 14357           20974   
111121     1115              1202                  2964           17453   
77337      1103               574                  2699            7986   
68705      1102              1052                  2568            8632   
252379     1221                80                  1528            4501   
508228     1500              1167                  1760           13401   
272756     1240               162                   851            5653   
13076       685                78                   845            2790   
235853     1204               114                   786            4807   
256880     1223                51                   652            3444   
104034     1112               550                   703            4724   
260324     1224               110                   627            4122   
958796     8841               231                   618            6127   
91077      1106               321                   620            6914   
15866       686               235                   448            2767   
536632     1504               192                   428            4478   
899689     7184               299                   456            4480   
168169     1151                83                   361            2126   
177170     1162               134                   371            3343   
704357     1620                61                   341            4525   
53342       694               126                   348            4499   
868721     2667               262                   309            6988   
172717     1160                94                   264            2225   
979231     9477                73                   325            5452   
206396     1182               107                   280            3730   
85323      1104               105                   281            5754   
97991      1110                90                   280            3388   
146237     1140               112                   246            4102   
46785       692               118                   273            5042   
170326     1153                42                   238            2391   
529114     1502               114                   246            4833   
521629     1501               138                   260            7485   
160947     1145                84                   193            3852   
692619     1604               150                   221            4339   
187067     1174                22                   185            2170   
228964     1202                23                   178            3391   
189237     1175                33                   176            2913   
174942     1161                48                   178            2228   
232355     1203                46                   159            3498   
660841     1584               127                   229            7749   
138240     1131                35                   152            1261   
459802     1406                74                   142            5415   
60736       699                86                   166            2418   
974281     9069                 6                   144             700   
813302     1762                84                   279            4427   
157649     1144                34                   123            3298   
182703     1172                16                   141            2190   
295853     1255                33                   128            2201   
998079     9712                40                   145            1155   
10249       684                45                   120            2827   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
18633                              4415                                12266   
111121                

In [160]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_nan_delay_sort_next_end['station_point'], grouped_nan_delay_sort_next_end['nextbike_trips_end_at_station_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_nan_delay_sort_next_end['station_point'], grouped_nan_delay_sort_next_end['nextbike_trips_end_at_station_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [158]:
grouped_nan_delay_sort_tier_end = grouped_nan_delay.sort_values(by='tier_trips_end_at_station_count', ascending=False).head(50)
grouped_nan_delay_sort_tier_end

stop_id  tier_trips_count  nextbike_trips_count  cancelled_trip  \
18633       687              5297                 14357           20974   
111121     1115              1202                  2964           17453   
68705      1102              1052                  2568            8632   
508228     1500              1167                  1760           13401   
104034     1112               550                   703            4724   
77337      1103               574                  2699            7986   
91077      1106               321                   620            6914   
899689     7184               299                   456            4480   
958796     8841               231                   618            6127   
868721     2667               262                   309            6988   
15866       686               235                   448            2767   
272756     1240               162                   851            5653   
536632     1504               192                   428            4478   
177170     1162               134                   371            3343   
692619     1604               150                   221            4339   
521629     1501               138                   260            7485   
53342       694               126                   348            4499   
85323      1104               105                   281            5754   
146237     1140               112                   246            4102   
235853     1204               114                   786            4807   
206396     1182               107                   280            3730   
1793        371               115                   117            5615   
97991      1110                90                   280            3388   
46785       692               118                   273            5042   
172717     1160                94                   264            2225   
260324     1224               110                   627            4122   
529114     1502               114                   246            4833   
160947     1145                84                   193            3852   
13076       685                78                   845            2790   
729773     1650                91                    88            2965   
168169     1151                83                   361            2126   
252379     1221                80                  1528            4501   
660841     1584               127                   229            7749   
459802     1406                74                   142            5415   
407114     1344                87                    45            4027   
394767     1341                92                    20            6408   
60736       699                86                   166            2418   
704357     1620                61                   341            4525   
928102     8507                71                   103            3023   
264446     1231                53                    79            3363   
174942     1161                48                   178            2228   
256880     1223                51                   652            3444   
212461     1184                48                   110            2724   
979231     9477                73                   325            5452   
401175     1342                48                    16            5939   
232355     1203                46                   159            3498   
142022     1135                41                    84            1222   
542141     1506                38                    59            1953   
245683     1212                38                   100            2408   
321118     1291                46                     7            3613   

        tier_trips_end_at_station_count  nextbike_trips_end_at_station_count  \
18633                              4415                                12266   
111121                

In [161]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(grouped_nan_delay_sort_tier_end['station_point'], grouped_nan_delay_sort_tier_end['tier_trips_end_at_station_count'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(grouped_nan_delay_sort_tier_end['station_point'], grouped_nan_delay_sort_tier_end['tier_trips_end_at_station_count']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

In [152]:
merged_nan_delay_sort_delay = grouped_nan_delay.sort_values(by='cancelled_trip', ascending=False).head(50)
merged_nan_delay_sort_delay

stop_id  tier_trips_count  nextbike_trips_count  cancelled_trip  \
18633       687              5297                 14357           20974   
111121     1115              1202                  2964           17453   
508228     1500              1167                  1760           13401   
68705      1102              1052                  2568            8632   
77337      1103               574                  2699            7986   
660841     1584               127                   229            7749   
521629     1501               138                   260            7485   
868721     2667               262                   309            6988   
91077      1106               321                   620            6914   
394767     1341                92                    20            6408   
958796     8841               231                   618            6127   
401175     1342                48                    16            5939   
85323      1104               105                   281            5754   
272756     1240               162                   851            5653   
1793        371               115                   117            5615   
979231     9477                73                   325            5452   
459802     1406                74                   142            5415   
944674     8811                17                     7            5170   
46785       692               118                   273            5042   
939740     8635                 7                    15            4934   
529114     1502               114                   246            4833   
235853     1204               114                   786            4807   
647128     1574                24                     1            4777   
104034     1112               550                   703            4724   
600186     1553                30                    17            4597   
604783     1554                34                    18            4561   
682640     1593                32                    68            4548   
704357     1620                61                   341            4525   
252379     1221                80                  1528            4501   
53342       694               126                   348            4499   
899689     7184               299                   456            4480   
536632     1504               192                   428            4478   
289950     1245                30                    21            4451   
813302     1762                84                   279            4427   
692619     1604               150                   221            4339   
619736     1562                15                    11            4270   
260324     1224               110                   627            4122   
146237     1140               112                   246            4102   
792921     1740                20                    11            4068   
674530     1591                15                    36            4063   
916212     8437                22                   103            4060   
150339     1141                33                    95            4050   
678593     1592                 9                    16            4047   
407114     1344                87                    45            4027   
734367     1655                34                    61            4020   
757393     1702                 8                    16            4015   
580538     1540                17                    24            3944   
624006     1563                 0                     5            3869   
160947     1145                84                   193            3852   
640360     1570                 7                     0            3834   

                   station_point                                  stop_name  \
18633   POINT (7.09713 50.73201)                                   Bonn Hbf   
111121  POINT (7.10248 5

In [154]:
import folium
from folium.plugins import HeatMap

# Create a map centered at a specific location
m = folium.Map(location=[50.73780, 7.10523], zoom_start=12)

# Create a HeatMap layer using the station_point and tier_trips_count columns
heat_data = [[point.y, point.x, count] for point, count in zip(merged_nan_delay_sort_delay['station_point'], merged_nan_delay_sort_delay['cancelled_trip'])]
HeatMap(heat_data).add_to(m)

# Add markers for each station_point
for point, count in zip(merged_nan_delay_sort_delay['station_point'], merged_nan_delay_sort_delay['cancelled_trip']):
    folium.CircleMarker(location=[point.y, point.x], radius=5, color='black', fill=True, fill_color='red', fill_opacity=0.7).add_to(m)

# Display the map
m

### Stations that had no trip at all

In [73]:
# load Bonn PT data and substract the stations from data to see whhich stations have no micromobilty rides at all

In [74]:
station_trip = data.groupby('stop_id').agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum'})
station_trip = station_trip.merge(data[['stop_id', 'station_point', 'stop_name', 'buffer_zone']], on='stop_id', how='left')
station_trip.drop_duplicates(inplace=True)

In [75]:
#station_trip = data.groupby('stop_id').agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum'})

In [76]:
no_trip = station_trip[(station_trip['tier_trips_count'] == 0) & (station_trip['nextbike_trips_count'] == 0)]
no_trip

stop_id  tier_trips_count  nextbike_trips_count  \
365939      1130                 0                     0   
369229      1132                 0                     0   
864933      1294                 0                     0   
872399      1296                 0                     0   
914081      1307                 0                     0   
1003131     1334                 0                     0   
1163357     1374                 0                     0   
1200143     1387                 0                     0   
1324689     1456                 0                     0   
1408991     1503                 0                     0   
1505907     1529                 0                     0   
1544473     1544                 0                     0   
1545943     1548                 0                     0   
1549401     1549                 0                     0   
1560647     1551                 0                     0   
1588481     1555                 0                     0   
1591939     1556                 0                     0   
1595397     1557                 0                     0   
1598855     1558                 0                     0   
1602313     1559                 0                     0   
1657744     1571                 0                     0   
1814995     1622                 0                     0   
1886744     1663                 0                     0   
1935921     1706                 0                     0   
1994988     1728                 0                     0   
2087283     1766                 0                     0   
2108452     1984                 0                     0   
2118765     2308                 0                     0   
2120733     2309                 0                     0   
2142568     2517                 0                     0   
2188312     2531                 0                     0   
2204350     2553                 0                     0   
2268063     5567                 0                     0   
2270120     5569                 0                     0   
2270154     5570                 0                     0   
2271987     6172                 0                     0   
2273808     6173                 0                     0   
2313341     7938                 0                     0   
2328923     8087                 0                     0   
2346514     8439                 0                     0   
2558548     9779                 0                     0   

                    station_point                     stop_name  \
365939   POINT (7.10177 50.72829)                Bonn Königstr.   
369229   POINT (7.10419 50.72198)          Bonn Rittershausstr.   
864933   POINT (7.09962 50.69983)           Bonn Don-Bosco-Str.   
872399   POINT (7.09726 50.70312)            Bonn Sertürnerstr.   
914081   POINT (7.09439 50.69108)                   Bonn Waldau   
1003131  POINT (7.04249 50.71984)            Bonn Alter Heerweg   
1163357  POINT (7.04134 50.69582)       Bonn Hardthöhe/Südwache   
1200143  POINT (7.05056 50.65580)           Bonn Professorenweg   
1324689  POINT (7.04906 50.73593)         Bonn Dransdorf Kirche   
1408991  POINT (7.12509 50.73989)        Bonn Obere Wilhelmstr.   
1505907  POINT (7.09608 50.74668)             Bonn Augustusring   
1544473  POINT (7.16635 50.72870)        Bonn Oberkasseler Str.   
1545943  POINT (7.17598 50.73431)              Bonn Am Waldrand   
1549401  POINT (7.18832 50.72545)              Bonn Oberholtorf   
1560647  POINT (7.14752 50.74096)           Bonn Im Thelenpfand   
1588481  POINT (7.18040 50.73406)            Bonn Bleibtreustr.   
1591939  POINT (7.18411 50.73304)      Bonn Niederholtorf Mitte   
1595397  POINT (7.18550 50.73083)     Bonn Niederholtorf Kirche   
1598855  POINT (7.19226 50.72868)                 Bonn Ungarten   
1602313  POINT (7.19591 50.73070)              Bonn Ettenhausen   
1657744  POINT (7.20191 50.74461)            Bonn Kleinfeldstr.   
1814995  POINT

In [77]:
# Ensure 'geometry' column exists in buffer_gdf
buffer_gdf = gpd.GeoDataFrame(no_trip, geometry='buffer_zone')
buffer_gdf['geometry'] = buffer_gdf['buffer_zone']

# Create a folium map
m = folium.Map(location=[buffer_gdf.geometry.centroid.y.mean(), buffer_gdf.geometry.centroid.x.mean()], zoom_start=12)

# Add buffer zones to the map
for _, row in buffer_gdf.iterrows():
    folium.GeoJson(row['geometry']).add_to(m)

# Display the map
m

In [78]:
trip = station_trip[(station_trip['tier_trips_count'] != 0) & (station_trip['nextbike_trips_count'] != 0)]
trip

stop_id  tier_trips_count  nextbike_trips_count  \
0             43                56                   123   
4611         371               299                   326   
20965        683                67                   214   
27545        684                89                   259   
34124        685               183                  1810   
...          ...               ...                   ...   
2546270     9712               141                   456   
2549893     9715                18                     5   
2553975     9777                12                     6   
2556962     9778                 1                     1   
2560675     9780                 5                    68   

                    station_point                                stop_name  \
0        POINT (7.07351 50.73910)                      Bonn Propsthof Nord   
4611     POINT (7.15835 50.68034)            Bonn Bad Godesberg Stadthalle   
20965    POINT (7.11452 50.72175)                       Bonn Museum Koenig   
27545    POINT (7.11158 50.72556)  Bonn Bundesrechnungshof/Auswärtiges Amt   
34124    POINT (7.10841 50.73009)                           Bonn Juridicum   
...                           ...                                      ...   
2546270  POINT (7.11800 50.71454)                        Bonn Un Campus Bf   
2549893  POINT (7.14143 50.70509)                       Bonn Heinemannstr.   
2553975  POINT (7.04793 50.74116)                         Bonn Kleine Str.   
2556962  POINT (7.07265 50.72710)                      Bonn Magdalenenstr.   
2560675  POINT (7.05240 50.75620)                     Bonn Georg-Elser-Weg   

                                               buffer_zone  
0        POLYGON ((7.07626 50.73943, 7.07630 50.73926, ...  
4611     POLYGON ((7.16110 50.68067, 7.16113 50.68050, ...  
20965    POLYGON ((7.11727 50.72208, 7.11731 50.72191, ...  
27545    POLYGON ((7.11433 50.72589, 7.11437 50.72572, ...  
34124    POLYGON ((7.11116 50.73043, 7.11120 50.73026, ...  
...                                                    ...  
2546270  POLYGON ((7.12075 50.71487, 7.12079 50.71470, ...  
2549893  POLYGON ((7.14418 50.70542, 7.14422 50.70525, ...  
2553975  POLYGON ((7.05068 50.74150, 7.05072 50.74133, ...  
2556962  POLYGON ((7.07540 50.72744, 7.07544 50.72727, ...  
2560675  POLYGON ((7.05515 50.75653, 7.05519 50.75636, ...  

[403 rows x 6 columns]

In [79]:
trip_tier_only = station_trip[(station_trip['tier_trips_count'] != 0) & (station_trip['nextbike_trips_count'] == 0)]
trip_tier_only

stop_id  tier_trips_count  nextbike_trips_count  \
759269      1244                22                     0   
922799      1309                 2                     0   
943344      1313                12                     0   
957316      1318                 3                     0   
1094178     1350                 6                     0   
1112087     1354                 5                     0   
1122454     1356                 1                     0   
1126895     1357                11                     0   
1141999     1362                 7                     0   
1151696     1365                 3                     0   
1155136     1371                13                     0   
1158921     1372                40                     0   
1169175     1375                 1                     0   
1177217     1381                14                     0   
1185652     1383                24                     0   
1193372     1385                 4                     0   
1197232     1386                 1                     0   
1208310     1404                 9                     0   
1299566     1448                 5                     0   
1608798     1561                 2                     0   
1633893     1565                13                     0   
1662039     1573                 4                     0   
1906692     1681                 3                     0   
1910289     1682                44                     0   
1915672     1684                 1                     0   
1919269     1686                 3                     0   
1921080     1687                 6                     0   
1935460     1705                 1                     0   
1936382     1707                12                     0   
1977256     1721                34                     0   
1983188     1722                20                     0   
1989120     1723                24                     0   
2054557     1746                 1                     0   
2093684     1957                13                     0   
2130837     2513                30                     0   
2133792     2514                 3                     0   
2136747     2516                10                     0   
2153677     2520                22                     0   
2180003     2529                36                     0   
2184439     2530                 2                     0   
2207993     2555                 8                     0   
2231885     2724                 5                     0   
2307727     7786                 7                     0   
2418783     8812                 1                     0   
2428291     8815                 7                     0   
2530560     9704                 1                     0   

                    station_point                      stop_name  \
759269   POINT (7.08535 50.71095)             Bonn Am Mühlenberg   
922799   POINT (7.08497 50.69134)                Bonn Haager Weg   
943344   POINT (7.06827 50.70689)        Bonn Lengsdorf Friedhof   
957316   POINT (7.06494 50.70821)           Bonn An Der Ziegelei   
1094178  POINT (7.03096 50.71226)           Bonn Medinghoven Tüv   
1112087  POINT (7.03949 50.71136)            Bonn Wesselheideweg   
1122454  POINT (7.04099 50.71011)                 Bonn Derlestr.   
1126895  POINT (7.03390 50.70655)        Bonn Hardtberg Klinikum   
1141999  POINT (7.04740 50.70607)       Bonn Hardthöhe/Nordwache   
1151696  POINT (7.04819 50.70748)             Bonn Ossietzkystr.   
1155136  POINT (7.05516 50.70372)    Bonn Hardtberg Schulzentrum   
1158921  POINT (7.05310 50.70034)               Bonn Riemannstr.   
1169175  POINT (7.04940 50.69731)               Bonn Reaumurstr.   
1177217  POINT (7.06970 50.69342)       Bonn Ückesdorf Gymnasium   
1185652  POINT (7.07385 50.68141)           Bonn Kurfürstenplatz   
1193372  POINT (7.06714 50.67393)              Bonn Merler Allee   
1197232  POINT (7.06553 50.67223

In [80]:
# Ensure 'geometry' column exists in buffer_gdf
buffer_gdf = gpd.GeoDataFrame(trip_tier_only, geometry='buffer_zone')
buffer_gdf['geometry'] = buffer_gdf['buffer_zone']

# Create a folium map
m = folium.Map(location=[buffer_gdf.geometry.centroid.y.mean(), buffer_gdf.geometry.centroid.x.mean()], zoom_start=12)

# Add buffer zones to the map
for _, row in buffer_gdf.iterrows():
    folium.GeoJson(row['geometry']).add_to(m)

# Display the map
m

In [81]:
trip_next_only = station_trip[(station_trip['tier_trips_count'] == 0) & (station_trip['nextbike_trips_count'] != 0)]
trip_next_only

stop_id  tier_trips_count  nextbike_trips_count  \
3115         161                 0                     6   
383286      1138                 0                     2   
452511      1152                 0                     2   
568860      1185                 0                    14   
648436      1211                 0                     4   
811890      1270                 0                     7   
815587      1273                 0                     1   
867555      1295                 0                     2   
879463      1297                 0                     1   
1153651     1370                 0                     2   
1464367     1515                 0                     9   
1619367     1563                 0                     9   
1889643     1665                 0                     1   
2164890     2525                 0                     1   
2206616     2554                 0                     2   
2241905     2742                 0                    10   
2306587     7729                 0                     1   
2307057     7784                 0                     3   
2311624     7891                 0                     4   
2322072     7982                 0                     2   
2323366     7983                 0                     9   
2385311     8607                 0                     1   
2551510     9716                 0                     2   

                    station_point                    stop_name  \
3115     POINT (7.15955 50.68392)        Bonn Bad Godesberg Bf   
383286   POINT (7.10049 50.71785)              Bonn Lotharstr.   
452511   POINT (7.09106 50.73890)                 Bonn Maxstr.   
568860   POINT (7.07870 50.74973)              Bonn Josephinum   
648436   POINT (7.07436 50.72625)         Bonn Magdalenenplatz   
811890   POINT (7.10860 50.71269)                Bonn Pützstr.   
815587   POINT (7.10938 50.70975)                Bonn Bergstr.   
867555   POINT (7.09303 50.69895)          Bonn Jugendherberge   
879463   POINT (7.09411 50.70048)          Bonn Haus Venusberg   
1153651  POINT (7.04555 50.70629)            Bonn Hardtbergbad   
1464367  POINT (7.11166 50.76310)                 Bonn Siegaue   
1619367  POINT (7.17971 50.74789)             Bonn Am Tanzberg   
1889643  POINT (7.15953 50.69631)              Bonn Mittelstr.   
2164890  POINT (7.07443 50.72752)               Bonn Frongasse   
2206616  POINT (7.05495 50.76098)             Bonn Lärchenstr.   
2241905  POINT (7.07872 50.69476)              Bonn Katzenloch   
2306587  POINT (7.12919 50.71512)        Bonn Fritz-Erler-Str.   
2307057  POINT (7.15070 50.75124)      Bonn Gesamtschule Beuel   
2311624  POINT (7.13317 50.69633)        Bonn Joseph-Roth-Str.   
2322072  POINT (7.18363 50.71131)            Bonn Humbroichweg   
2323366  POINT (7.17912 50.71081)       Bonn Am Kriegersgraben   
2385311  POINT (7.12684 50.71657)   Bonn Heinrich-Brüning-Str.   
2551510  POINT (7.06063 50.73597)  Bonn Gerhart-Hauptmann-Str.   

                                               buffer_zone  
3115     POLYGON ((7.16230 50.68425, 7.16234 50.68408, ...  
383286   POLYGON ((7.10324 50.71819, 7.10328 50.71801, ...  
452511   POLYGON ((7.09381 50.73923, 7.09384 50.73906, ...  
568860   POLYGON ((7.08145 50.75006, 7.08149 50.74989, ...  
648436   POLYGON ((7.07711 50.72659, 7.07715 50.72641, ...  
811890   POLYGON ((7.11135 50.71302, 7.11139 50.71285, ...  
815587   POLYGON ((7.11213 50.71008, 7.11217 50.70991, ...  
867555   POLYGON ((7.09578 50.69928, 7.09582 50.69911, ...  
879463   POLYGON ((7.09686 50.70082, 7.09690 50.70064, ...  
1153651  POLYGON ((7.04830 50.70663, 7.04834 50.70646, ...  
1464367  POLYGON ((7.11441 50.76343, 7.11445 50.76326, ...  
1619367  POLYGON ((7.18246 50.74823, 7.18250 50.74805, ...  
1889643  POLYGON ((7.16228 50.69664, 7.16232 50.69647, ...  
2164890  POLYGON ((7.07718 50.72785, 7.07722 50.72768, ...  
2206616  POLYGON ((7.05770 50.76131, 7.05774 50.76114, ...  
2241905

In [82]:
# Ensure 'geometry' column exists in buffer_gdf
buffer_gdf = gpd.GeoDataFrame(trip_next_only, geometry='buffer_zone')
buffer_gdf['geometry'] = buffer_gdf['buffer_zone']

# Create a folium map
m = folium.Map(location=[buffer_gdf.geometry.centroid.y.mean(), buffer_gdf.geometry.centroid.x.mean()], zoom_start=12)

# Add buffer zones to the map
for _, row in buffer_gdf.iterrows():
    folium.GeoJson(row['geometry']).add_to(m)

# Display the map
m

In [83]:
trip_next_only.info()

<class 'pandas.core.frame.DataFrame'>
Index: 23 entries, 3115 to 2551510
Data columns (total 6 columns):
 #   Column                Non-Null Count  Dtype   
---  ------                --------------  -----   
 0   stop_id               23 non-null     int64   
 1   tier_trips_count      23 non-null     int64   
 2   nextbike_trips_count  23 non-null     int64   
 3   station_point         23 non-null     geometry
 4   stop_name             23 non-null     object  
 5   buffer_zone           23 non-null     geometry
dtypes: geometry(2), int64(3), object(1)
memory usage: 1.3+ KB


In [84]:
no_trip = gpd.GeoDataFrame(no_trip, geometry='buffer_zone')

In [85]:
no_trip = no_trip.set_crs(epsg=4326)

In [86]:
trip = gpd.GeoDataFrame(trip, geometry='buffer_zone')

In [87]:
trip = trip.set_crs(epsg=4326)

In [88]:
trip_tier_only = gpd.GeoDataFrame(trip_tier_only, geometry='buffer_zone')

In [89]:
trip_tier_only = trip_tier_only.set_crs(epsg=4326)

In [90]:
trip_next_only = gpd.GeoDataFrame(trip_next_only, geometry='buffer_zone')

In [91]:
trip_next_only = trip_next_only.set_crs(epsg=4326)

In [92]:
#no_trip.rename(columns={'station_point': 'geometry'}, inplace = True)

In [93]:
import folium

# Create a folium map object centered at the coordinates of Bonn
m = folium.Map(location=[50.73743, 7.09821], zoom_start=12)

# Add the buffer zones of each dataset to the map
folium.GeoJson(no_trip['buffer_zone'], name='No_Trip', style_function=lambda x: {'color': 'red'}).add_to(m)
folium.GeoJson(trip['buffer_zone'], name='Trip', style_function=lambda x: {'color': 'blue'}).add_to(m)
folium.GeoJson(trip_tier_only['buffer_zone'], name='Tier only', style_function=lambda x: {'color': 'green'}).add_to(m)
folium.GeoJson(trip_next_only['buffer_zone'], name='next only', style_function=lambda x: {'color': 'yellow'}).add_to(m)


# Add a layer control to the map
folium.LayerControl().add_to(m)

# Display the map
m

In [94]:
# AUF STATION LEVEL DANN RUNTERBRECHEN UND ANSCHAUEN 

In [95]:
# AGGREGATE FOR EACH STATION AND EACH DAY

In [96]:
data1 = data.copy()

In [97]:
data['scheduled_arrival_time'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 2564861 entries, 0 to 2564860
Series name: scheduled_arrival_time
Non-Null Count    Dtype         
--------------    -----         
2564861 non-null  datetime64[ns]
dtypes: datetime64[ns](1)
memory usage: 19.6 MB


In [98]:
data1['date'] = data['scheduled_arrival_time']

In [99]:
data1.set_index('date', inplace=True)

In [100]:
data1

route_id  agency_id route_short_name  route_type  \
date                                                                    
2023-06-30 01:40:00       551          8              551           3   
2023-06-30 01:42:00       551          8              551           3   
2023-06-30 01:44:00       551          8              551           3   
2023-06-30 01:46:00       551          8              551           3   
2023-06-30 01:49:00       551          8              551           3   
...                       ...        ...              ...         ...   
2023-08-01 03:21:00       689          6               N9           3   
2023-08-01 03:22:00       689          6               N9           3   
2023-08-01 03:23:00       689          6               N9           3   
2023-08-01 03:24:00       682          6               N2           3   
2023-08-01 03:25:00       689          6               N9           3   

                    route_type_name                               agency_name  \
date                                                                            
2023-06-30 01:40:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:42:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:44:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:46:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:49:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
...                             ...                                       ...   
2023-08-01 03:21:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:22:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:23:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:24:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:25:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   

                     service_id  \
date                              
2023-06-30 01:40:00         125   
2023-06-30 01:42:00         125   
2023-06-30 01:44:00         125   
2023-06-30 01:46:00         125   
2023-06-30 01:49:00         125   
...                         ...   
2023-08-01 03:21:00          43   
2023-08-01 03:22:00          43   
2023-08-01 03:23:00          43   
2023-08-01 03:24:00          43   
2023-08-01 03:25:00          43   

                                                               trip_id  \
date                                                                     
2023-06-30 01:40:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:42:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:44:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:46:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:49:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
...                                                                ...   
2023-08-01 03:21:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2023-08-01 03:22:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2023-08-01 03:23:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2023-08-01 03:24:00  6820005-682-006-687.2.34:263500-46-1_8BA968F1-...   
2023-08-01 03:25:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   

                    trip_headsign  direction_id  ...  delay_span  \
date                                             ...               
2023-06-30 01:40:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:42:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:44:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:46:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:49:00  Troisdorf Bf             0  ...           0   
...                           ...           ...  ...         ...   
2023-08-01 03:21:00      Bonn Hbf             0  ...  

In [101]:
data1.index = pd.to_datetime(data1.index)

In [102]:
data1

route_id  agency_id route_short_name  route_type  \
date                                                                    
2023-06-30 01:40:00       551          8              551           3   
2023-06-30 01:42:00       551          8              551           3   
2023-06-30 01:44:00       551          8              551           3   
2023-06-30 01:46:00       551          8              551           3   
2023-06-30 01:49:00       551          8              551           3   
...                       ...        ...              ...         ...   
2023-08-01 03:21:00       689          6               N9           3   
2023-08-01 03:22:00       689          6               N9           3   
2023-08-01 03:23:00       689          6               N9           3   
2023-08-01 03:24:00       682          6               N2           3   
2023-08-01 03:25:00       689          6               N9           3   

                    route_type_name                               agency_name  \
date                                                                            
2023-06-30 01:40:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:42:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:44:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:46:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
2023-06-30 01:49:00             Bus  RSVG Rhein-Sieg-Verkehrsgesellschaft mbH   
...                             ...                                       ...   
2023-08-01 03:21:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:22:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:23:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:24:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   
2023-08-01 03:25:00             Bus         SWB Stadtwerke Bonn Verkehrs GmbH   

                     service_id  \
date                              
2023-06-30 01:40:00         125   
2023-06-30 01:42:00         125   
2023-06-30 01:44:00         125   
2023-06-30 01:46:00         125   
2023-06-30 01:49:00         125   
...                         ...   
2023-08-01 03:21:00          43   
2023-08-01 03:22:00          43   
2023-08-01 03:23:00          43   
2023-08-01 03:24:00          43   
2023-08-01 03:25:00          43   

                                                               trip_id  \
date                                                                     
2023-06-30 01:40:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:42:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:44:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:46:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
2023-06-30 01:49:00  93-551-008-687.2.36:014000-33-157_49E69401-92E...   
...                                                                ...   
2023-08-01 03:21:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2023-08-01 03:22:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2023-08-01 03:23:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   
2023-08-01 03:24:00  6820005-682-006-687.2.34:263500-46-1_8BA968F1-...   
2023-08-01 03:25:00  6890005-689-006-687.2.34:263500-53-1_2AFE8F0F-...   

                    trip_headsign  direction_id  ...  delay_span  \
date                                             ...               
2023-06-30 01:40:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:42:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:44:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:46:00  Troisdorf Bf             0  ...           0   
2023-06-30 01:49:00  Troisdorf Bf             0  ...           0   
...                           ...           ...  ...         ...   
2023-08-01 03:21:00      Bonn Hbf             0  ...  

In [103]:
agg_stop_date = data1.groupby(['stop_name', 'stop_id', data1.index.date]).agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'arrival_delay' : 'mean'})

In [104]:
agg_stop_date

tier_trips_count  \
stop_name           stop_id                                
Bonn Adelheidisstr. 1512    2023-07-01                 0   
                            2023-07-02                 0   
                            2023-07-03                 5   
                            2023-07-04                 2   
                            2023-07-05                 3   
...                                                  ...   
Bonn Ürziger Str.   1634    2023-07-28                 1   
                            2023-07-29                 0   
                            2023-07-30                 0   
                            2023-07-31                 0   
                            2023-08-01                 0   

                                        nextbike_trips_count  \
stop_name           stop_id                                    
Bonn Adelheidisstr. 1512    2023-07-01                     0   
                            2023-07-02                     2   
                            2023-07-03                     2   
                            2023-07-04                     0   
                            2023-07-05                     0   
...                                                      ...   
Bonn Ürziger Str.   1634    2023-07-28                     1   
                            2023-07-29                     0   
                            2023-07-30                     0   
                            2023-07-31                     0   
                            2023-08-01                     0   

                                                   arrival_delay  
stop_name           stop_id                                       
Bonn Adelheidisstr. 1512    2023-07-01           0 days 00:00:00  
                            2023-07-02           0 days 00:00:00  
                            2023-07-03 0 days 00:00:07.720588235  
                            2023-07-04 0 days 00:00:07.815126050  
                            2023-07-05    0 days 00:00:08.640000  
...                                                          ...  
Bonn Ürziger Str.   1634    2023-07-28 0 days 00:00:06.666666666  
                            2023-07-29 0 days 00:00:16.071428571  
                            2023-07-30 0 days 00:00:12.631578947  
                            2023-07-31 0 days 00:00:06.923076923  
                            2023-08-01                       NaT  

[16013 rows x 3 columns]

In [105]:
times = pd.DatetimeIndex(data1.scheduled_arrival_time)
grouped = data1.groupby([times.hour, times.minute])

In [106]:
times

DatetimeIndex(['2023-06-30 01:40:00', '2023-06-30 01:42:00',
               '2023-06-30 01:44:00', '2023-06-30 01:46:00',
               '2023-06-30 01:49:00', '2023-06-30 01:51:00',
               '2023-06-30 01:53:00', '2023-06-30 01:55:00',
               '2023-06-30 02:40:00', '2023-06-30 02:42:00',
               ...
               '2023-08-01 03:19:00', '2023-08-01 03:19:00',
               '2023-08-01 03:20:00', '2023-08-01 03:20:00',
               '2023-08-01 03:21:00', '2023-08-01 03:21:00',
               '2023-08-01 03:22:00', '2023-08-01 03:23:00',
               '2023-08-01 03:24:00', '2023-08-01 03:25:00'],
              dtype='datetime64[ns]', name='scheduled_arrival_time', length=2564861, freq=None)

In [107]:
agg_station_date_hour = data1.groupby(['stop_name', 'stop_id', data1['scheduled_arrival_time'].dt.date, data1['scheduled_arrival_time'].dt.hour]).agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'arrival_delay' : 'mean'})

In [108]:
agg_station_date_hour

tier_trips_count  \
stop_name           stop_id scheduled_arrival_time scheduled_arrival_time                     
Bonn Adelheidisstr. 1512    2023-07-01             1                                      0   
                                                   2                                      0   
                                                   3                                      0   
                                                   4                                      0   
                                                   5                                      0   
...                                                                                     ...   
Bonn Ürziger Str.   1634    2023-07-31             19                                     0   
                                                   20                                     0   
                                                   21                                     0   
                                                   22                                     0   
                            2023-08-01             1                                      0   

                                                                           nextbike_trips_count  \
stop_name           stop_id scheduled_arrival_time scheduled_arrival_time                         
Bonn Adelheidisstr. 1512    2023-07-01             1                                          0   
                                                   2                                          0   
                                                   3                                          0   
                                                   4                                          0   
                                                   5                                          0   
...                                                                                         ...   
Bonn Ürziger Str.   1634    2023-07-31             19                                         0   
                                                   20                                         0   
                                                   21                                         0   
                                                   22                                         0   
                            2023-08-01             1                                          0   

                                                                          arrival_delay  
stop_name           stop_id scheduled_arrival_time scheduled_arrival_time                
Bonn Adelheidisstr. 1512    2023-07-01             1                             0 days  
                                                   2                             0 days  
                                                   3                             0 days  
                                                   4                             0 days  
                                                   5                             0 days  
...                                                                                 ...  
Bonn Ürziger Str.   1634    2023-07-31             19                            0 days  
                                                   20                            0 days  
                                                   21                            0 days  
                                                   22                            0 days  
                            2023-08-01             1                                NaT  

[309714 rows x 3 columns]

In [109]:
agg_station_date_10min = data.groupby(['stop_id', 'stop_name', pd.Grouper(key='scheduled_arrival_time', freq='10Min')]).sum(numeric_only=True)

In [110]:
agg_station_date_10min

route_id  agency_id  \
stop_id stop_name            scheduled_arrival_time                        
43      Bonn Propsthof Nord  2023-07-01 00:50:00           16          1   
                             2023-07-01 01:20:00           16          1   
                             2023-07-01 01:50:00           32          2   
                             2023-07-01 02:00:00           16          1   
                             2023-07-01 02:50:00           16          1   
...                                                       ...        ...   
9780    Bonn Georg-Elser-Weg 2023-07-31 22:50:00          604          6   
                             2023-07-31 23:10:00          604          6   
                             2023-07-31 23:20:00          604          6   
                             2023-07-31 23:40:00          604          6   
                             2023-08-01 00:10:00          604          6   

                                                     route_type  service_id  \
stop_id stop_name            scheduled_arrival_time                           
43      Bonn Propsthof Nord  2023-07-01 00:50:00              0       11525   
                             2023-07-01 01:20:00              0       11525   
                             2023-07-01 01:50:00              0       23061   
                             2023-07-01 02:00:00              0       11525   
                             2023-07-01 02:50:00              0       11525   
...                                                         ...         ...   
9780    Bonn Georg-Elser-Weg 2023-07-31 22:50:00              3          43   
                             2023-07-31 23:10:00              3          43   
                             2023-07-31 23:20:00              3          43   
                             2023-07-31 23:40:00              3          43   
                             2023-08-01 00:10:00              3          43   

                                                     direction_id  shape_id  \
stop_id stop_name            scheduled_arrival_time                           
43      Bonn Propsthof Nord  2023-07-01 00:50:00                0      3176   
                             2023-07-01 01:20:00                0      3203   
                             2023-07-01 01:50:00                0      6329   
                             2023-07-01 02:00:00                1      3230   
                             2023-07-01 02:50:00                0      3021   
...                                                           ...       ...   
9780    Bonn Georg-Elser-Weg 2023-07-31 22:50:00                1      5633   
                             2023-07-31 23:10:00                0      5377   
                             2023-07-31 23:20:00                1      5633   
                             2023-07-31 23:40:00                0      5377   
                             2023-08-01 00:10:00                0      5377   

                                                     vrs_timestamp  \
stop_id stop_name            scheduled_arrival_time                  
43      Bonn Propsthof Nord  2023-07-01 00:50:00               308   
                             2023-07-01 01:20:00              1304   
                             2023-07-01 01:50:00              7108   
                             2023-07-01 02:00:00              1304   
                             2023-07-01 02:50:00             14304   
...                                                            ...   
9780    Bonn Georg-Elser-Weg 2023-07-31 22:50:00            220312   
                             2023-07-31 23:10:00            213806   
                             2023-07-31 23:20:00            223304   
                             2023-07-31 23:40:00            214807   
                             2023-08-01 00:10:00            221806   

                                                     stop_sequence  service  \
stop_id stop_name 

In [111]:
hourly_data = data.groupby(['stop_id', 'stop_name', pd.Grouper(key='scheduled_arrival_time', freq='10Min')]).agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'arrival_delay' : 'mean'})

In [112]:
hourly_data

tier_trips_count  \
stop_id stop_name            scheduled_arrival_time                     
43      Bonn Propsthof Nord  2023-07-01 00:50:00                    0   
                             2023-07-01 01:20:00                    0   
                             2023-07-01 01:50:00                    0   
                             2023-07-01 02:00:00                    0   
                             2023-07-01 02:50:00                    0   
...                                                               ...   
9780    Bonn Georg-Elser-Weg 2023-07-31 22:50:00                    0   
                             2023-07-31 23:10:00                    0   
                             2023-07-31 23:20:00                    0   
                             2023-07-31 23:40:00                    0   
                             2023-08-01 00:10:00                    0   

                                                     nextbike_trips_count  \
stop_id stop_name            scheduled_arrival_time                         
43      Bonn Propsthof Nord  2023-07-01 00:50:00                        0   
                             2023-07-01 01:20:00                        0   
                             2023-07-01 01:50:00                        0   
                             2023-07-01 02:00:00                        0   
                             2023-07-01 02:50:00                        0   
...                                                                   ...   
9780    Bonn Georg-Elser-Weg 2023-07-31 22:50:00                        0   
                             2023-07-31 23:10:00                        0   
                             2023-07-31 23:20:00                        0   
                             2023-07-31 23:40:00                        0   
                             2023-08-01 00:10:00                        0   

                                                      arrival_delay  
stop_id stop_name            scheduled_arrival_time                  
43      Bonn Propsthof Nord  2023-07-01 00:50:00    0 days 00:00:00  
                             2023-07-01 01:20:00    0 days 00:00:00  
                             2023-07-01 01:50:00    0 days 00:00:00  
                             2023-07-01 02:00:00    0 days 00:00:00  
                             2023-07-01 02:50:00    0 days 00:00:00  
...                                                             ...  
9780    Bonn Georg-Elser-Weg 2023-07-31 22:50:00    0 days 00:00:00  
                             2023-07-31 23:10:00                NaT  
                             2023-07-31 23:20:00    0 days 00:00:00  
                             2023-07-31 23:40:00    0 days 00:00:15  
                             2023-08-01 00:10:00                NaT  

[1290080 rows x 3 columns]

In [113]:
agg_station = data.groupby(['stop_name', 'stop_id']).agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'arrival_delay' : 'mean'})
agg_station

tier_trips_count  \
stop_name                          stop_id                     
Bonn Adelheidisstr.                1512                   43   
Bonn Agentur Für Arbeit            1364                    3   
Bonn Agnetendorfer Str.            9478                   52   
Bonn Ahrstr./Deutsches Museum Bonn 1519                   19   
Bonn Akazienweg                    1721                   34   
...                                                      ...   
Bonn Zum Wingertsberg              1038                    6   
Bonn Zur Autobahn                  2310                    2   
Bonn Ückesdorf Gymnasium           1381                   14   
Bonn Ückesdorf Mitte               1382                   32   
Bonn Ürziger Str.                  1634                    5   

                                            nextbike_trips_count  \
stop_name                          stop_id                         
Bonn Adelheidisstr.                1512                       82   
Bonn Agentur Für Arbeit            1364                       12   
Bonn Agnetendorfer Str.            9478                       62   
Bonn Ahrstr./Deutsches Museum Bonn 1519                       22   
Bonn Akazienweg                    1721                        0   
...                                                          ...   
Bonn Zum Wingertsberg              1038                        2   
Bonn Zur Autobahn                  2310                        1   
Bonn Ückesdorf Gymnasium           1381                        0   
Bonn Ückesdorf Mitte               1382                        1   
Bonn Ürziger Str.                  1634                       20   

                                                       arrival_delay  
stop_name                          stop_id                            
Bonn Adelheidisstr.                1512    0 days 00:00:10.560344827  
Bonn Agentur Für Arbeit            1364    0 days 00:00:14.118165784  
Bonn Agnetendorfer Str.            9478              0 days 00:00:00  
Bonn Ahrstr./Deutsches Museum Bonn 1519    0 days 00:00:14.602122015  
Bonn Akazienweg                    1721    0 days 00:00:15.946830801  
...                                                              ...  
Bonn Zum Wingertsberg              1038    0 days 00:00:16.294536817  
Bonn Zur Autobahn                  2310    0 days 00:00:10.262669962  
Bonn Ückesdorf Gymnasium           1381    0 days 00:00:24.272287862  
Bonn Ückesdorf Mitte               1382              0 days 00:00:00  
Bonn Ürziger Str.                  1634    0 days 00:00:10.306513409  

[513 rows x 3 columns]

In [114]:
agg_station_delayspan = data.groupby(['stop_name', 'stop_id', 'delay_span']).agg({'tier_trips_count': 'sum', 'nextbike_trips_count': 'sum', 'arrival_delay' : 'mean'})
agg_station_delayspan

tier_trips_count  \
stop_name                stop_id delay_span                     
Bonn Adelheidisstr.      1512    0                         34   
                                 0-5                        9   
                                 20-30                      0   
                                 30-45                      0   
                                 5-10                       0   
...                                                       ...   
Bonn Ückesdorf Gymnasium 1381    0                          7   
                                 0-5                        7   
Bonn Ückesdorf Mitte     1382    0                         32   
Bonn Ürziger Str.        1634    0                          4   
                                 0-5                        1   

                                             nextbike_trips_count  \
stop_name                stop_id delay_span                         
Bonn Adelheidisstr.      1512    0                             64   
                                 0-5                           18   
                                 20-30                          0   
                                 30-45                          0   
                                 5-10                           0   
...                                                           ...   
Bonn Ückesdorf Gymnasium 1381    0                              0   
                                 0-5                            0   
Bonn Ückesdorf Mitte     1382    0                              1   
Bonn Ürziger Str.        1634    0                             12   
                                 0-5                            8   

                                                        arrival_delay  
stop_name                stop_id delay_span                            
Bonn Adelheidisstr.      1512    0                    0 days 00:00:00  
                                 0-5                  0 days 00:00:30  
                                 20-30                0 days 00:24:57  
                                 30-45                0 days 00:00:00  
                                 5-10                 0 days 00:06:20  
...                                                               ...  
Bonn Ückesdorf Gymnasium 1381    0                    0 days 00:00:00  
                                 0-5        0 days 00:00:25.781517398  
Bonn Ückesdorf Mitte     1382    0                    0 days 00:00:00  
Bonn Ürziger Str.        1634    0                    0 days 00:00:00  
                                 0-5        0 days 00:00:11.318373071  

[1109 rows x 3 columns]